In [1]:
import json, requests, xml
from xml.dom import minidom
# %pip install ipyleaflet
from ipyleaflet import (Map, GeoData, basemaps, WidgetControl, GeoJSON,
   LayersControl, Icon, Marker, basemap_to_tiles, Choropleth,
   MarkerCluster, Heatmap, SearchControl, 
   FullScreenControl)


In [2]:
def show_features_on_map( query_response ):
  data = query_response.json()
  center = [38.128, 2.588]
  zoom = 3
  m = Map(basemap=basemaps.OpenStreetMap.Mapnik, center=center, zoom=zoom)
  geolayer = GeoJSON(
    name = 'Features',
    data=data,
    style={ 'opacity': 1, 'dashArray': '9', 'fillOpacity': 0.7, 'weight': 1 },
    hover_style={ 'color': 'white', 'dashArray': '0', 'fillOpacity': 0.5 }
  )
  m.add_layer(geolayer)
  m.add_control(FullScreenControl())
  m.add_control(LayersControl(position='topright'))
  d = m.layers[1].data   # contains featurecollection or feature
  key = 'features'
  if key in d:
    if (len(d[key])<1) : return m
    d = d[key][0]  # use first feature of collection
  key = 'bbox'
  if key in d:
    c = d[key]
    m.fit_bounds([[ c[1],c[0] ],[ c[3], c[2] ]])
  return m


# FedEO API Tutorial - PART 1: OpenSearch and API Features  
 This tutorial is part of a series of tutorials covering related subjects:                  

 * FedEO API Tutorial - PART 1: OpenSearch and API Features 
 * [FedEO API Tutorial - PART 2: STAC](tutorial-2-stac.ipynb)
 * [FedEO API Tutorial - PART 3: SPARQL Online](tutorial-3-sparql-online.ipynb)
 * [FedEO API Tutorial - PART 4: SPARQL Offline](tutorial-4-sparql.ipynb)


<a name='Overview'></a>     
## Overview  
 The different parts of the API covered in this Notebook are:    
 * [LandingPage](#LandingPage)
 * StacCollection
 * [Collections](#Collections)
 * [Collection](#Collection)
 * [APIDefinition](#APIDefinition)
 * [Features](#Features)
 * [Feature](#Feature)
      - [Collection](#Feature--EO-Collection)
      - [Service](#Feature--EO-Service)
      - [Granule](#Feature--EO-Granule)   
 


<a name='LandingPage'></a>     
## LandingPage  
 The LandingPage of the API is available at the `/` path.  It is available in multiple representations
 according to multiple profiles.  The API supports content negotiation.  The preferred media type can either
 be requested by using the `Accept` request HTTP header of by using the `httpAccept` query parameter. 
      
 ![LandingPage](https://plantuml-server.kkeisuke.dev/png/ZP91Jm8n48Nlyoicwq4D4HFFX02B4Cqg1FRWWSlO7PULRalQRbPZ_EyM4UaQ8FRGf7tVctcTj6ST6LUL4W18IbsNnLkXSW2xAjIQ39KeTBdMYfMRktV9wDcRGEqRe-jOIsrm84ci0YcMPEr0cupD4M1N-HGqUNvbSO20PP4nYi88oN2EtwTEPyPMLqPmjxkJx5BNNXYplfzF7lVtlvOxvTYyKEW1hnQxQup2iWiLHqWMOyFaUEItoZ2UJMLL0kmz2QdCpt5A-PzKMnG_0FrgZM_JYqluz0r1RAQrwRMDkL11YSZdQUXNoN233ED-YZ4vaZgFC8Hcmr7hwI4v3QMLSP8FC01Hs1tRcQvLkzlqDF8TvNsGwvyW3UIu8tZV_reS6XY2VqMFLUQ_wnS0.png)


    
**Example: 2**  
>  Representation: JSON   
> Requirement:  EOVOC-CCAT-IF-031030 (1)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: application/json'
> ```


In [3]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -180,
          -90,
          180,
          90
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          null,
          null
        ]
      ]
    }
  },
  "stac_version": "1.0.0-rc.2",
  "license": "various",
  "description": "FedEO Clearinghouse provides interoperable access, following ISO/OGC interface guidelines, to Earth Observation metadata",
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be",
      "type": "application/json",
      "title": "This document"
    },
    {
      "rel": "search",
      "href": "https://eovoc.spacebel.be/api?httpAccept=application/opensearchdescription%2Bxml",
      "type": "application/opensearchdescription+xml",
      "title": "The OpenSearch Description Document"
    },
    {
      "rel": "service-desc",
      "href": "https://eovoc.spacebel.be/api?httpAccept=application/openapi%2Bjson;version=3.0",
      "type": "applicat

**Example: 3**  
>  Representation: JSON-LD (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031030 (2)  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: application/ld+json'
> ```


In [4]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'application/ld+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "@type": "dcat:DataService",
  "dcat:qualifiedRelation": [
    {
      "dct:relation": "https://eovoc.spacebel.be",
      "dct:format": {
        "rdfs:label": "application/ld+json",
        "@type": "dct:MediaType"
      },
      "@type": "dcat:Relationship",
      "dct:title": "Self as JSON-LD (GeoDCAT-AP)",
      "dcat:hadRole": "http://www.iana.org/assignments/relation/self"
    },
    {
      "dct:relation": "https://eovoc.spacebel.be/api?httpAccept=application/opensearchdescription%2Bxml",
      "dct:format": {
        "rdfs:label": "application/opensearchdescription+xml",
        "@type": "dct:MediaType"
      },
      "@type": "dcat:Relationship",
      "dct:title": "The OpenSearch Description Document",
      "dcat:hadRole": "http://www.iana.org/assignments/relation/search"
    },
    {
      "dct:relation": "https://eovoc.spacebel.be/api?httpAccept=application/openapi%2Bjson;version=3.0",
      "dct:format": {
        "rdfs:label": "application/openapi+json;version=3.0",


**Example: 4**  
>  Representation: JSON-LD (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031030 (2)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: application/ld+json;profile="https://schema.org"'
> ```


In [5]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'application/ld+json;profile="https://schema.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "@type": "WebAPI",
  "documentation": [
    {
      "@type": "LinkRole",
      "encodingFormat": "application/json",
      "description": "This document",
      "linkRelationship": "self",
      "url": "https://eovoc.spacebel.be"
    },
    {
      "@type": "LinkRole",
      "encodingFormat": "application/opensearchdescription+xml",
      "description": "The OpenSearch Description Document",
      "linkRelationship": "search",
      "url": "https://eovoc.spacebel.be/api?httpAccept=application/opensearchdescription%2Bxml"
    },
    {
      "@type": "LinkRole",
      "encodingFormat": "application/openapi+json;version=3.0",
      "description": "The OpenAPI definition in JSON format",
      "linkRelationship": "service-desc",
      "url": "https://eovoc.spacebel.be/api?httpAccept=application/openapi%2Bjson;version=3.0"
    },
    {
      "@type": "LinkRole",
      "encodingFormat": "application/json;profile=\"http://explain.z3950.org/dtd/2.0/\"",
      "description": "The Explain Do

**Example: 5**  
>  Representation: RDF/XML (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031030 (3)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: application/rdf+xml'
> ```


In [6]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'application/rdf+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:DataService rdf:about="https://eovoc.spacebel.be">
      

**Example: 6**  
>  Representation: RDF/XML (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031030 (3)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: application/rdf+xml;profile="https://schema.org"'
> ```


In [7]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'application/rdf+xml;profile="https://schema.org"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:schema="https://schema.org/" xmlns:wikidata="http://www.wikidata.org/entity/" xmlns:rdfa="http://www.w3.org/ns/rdfa#" xmlns:snomed="http://purl.bioontology.org/ontology/SNOMEDCT/" xmlns:yago="http://yago-knowledge.org/resource/" xmlns:dbpedia="http://dbpedia.org/resource/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:void="http://rdfs.org/ns/void#" xmlns:dcterms="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:dctype="http://purl.org/dc/dcmitype/" xmlns:eli="http://data.europa.eu/eli/ontology#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:bibo="http://purl.org/ontology/bibo/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <schema:WebAPI rdf:about="https://eovoc.spacebel.be">
      
    
      <schema:documentati

**Example: 7**  
>  Representation: Turtle (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031030 (4)  
  OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: text/turtle'
> ```


In [8]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'text/turtle'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://eovoc.spacebel.be>
        a 

**Example: 8**  
>  Representation: Turtle (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031030 (4)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: text/turtle;profile="https://schema.org"'
> ```


In [9]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'text/turtle;profile="https://schema.org"'})
print(response.text)


@prefix schema: <https://schema.org/> .
@prefix void:  <http://rdfs.org/ns/void#> .
@prefix eli:   <http://data.europa.eu/eli/ontology#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix snomed: <http://purl.bioontology.org/ontology/SNOMEDCT/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix yago:  <http://yago-knowledge.org/resource/> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix dbpedia: <http://dbpedia.org/resource/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix rdf:   <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dctype: <http://purl.org/dc/dcmitype/> .
@prefix rdfa:  <http://www.w3.org/ns/rdfa#> .
@prefix dcterms: <http://purl.org/dc/terms/> .
@prefix bibo:  <http://purl.org/ontology/bibo/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix wikidata: <http://www.wikidata.org/entity/> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl

**Example: 9**  
>  Representation: JSON-LD (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031035 (1)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: application/ld+json;profile="http://data.europa.eu/930/"'
> ```


In [10]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'application/ld+json;profile="http://data.europa.eu/930/"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "@type": "dcat:DataService",
  "dcat:qualifiedRelation": [
    {
      "dct:relation": "https://eovoc.spacebel.be",
      "dct:format": {
        "rdfs:label": "application/ld+json;profile=\"http://data.europa.eu/930/\"",
        "@type": "dct:MediaType"
      },
      "@type": "dcat:Relationship",
      "dct:title": "Self as JSON-LD (GeoDCAT-AP)",
      "dcat:hadRole": "http://www.iana.org/assignments/relation/self"
    },
    {
      "dct:relation": "https://eovoc.spacebel.be/api?httpAccept=application/opensearchdescription%2Bxml",
      "dct:format": {
        "rdfs:label": "application/opensearchdescription+xml",
        "@type": "dct:MediaType"
      },
      "@type": "dcat:Relationship",
      "dct:title": "The OpenSearch Description Document",
      "dcat:hadRole": "http://www.iana.org/assignments/relation/search"
    },
    {
      "dct:relation": "https://eovoc.spacebel.be/api?httpAccept=application/openapi%2Bjson;version=3.0",
      "dct:format": {
        "rdfs:label": "

**Example: 10**  
>  Representation: RDF/XML (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031035 (2)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: application/rdf+xml;profile="http://data.europa.eu/930/"'
> ```


In [11]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'application/rdf+xml;profile="http://data.europa.eu/930/"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:DataService rdf:about="https://eovoc.spacebel.be">
      

**Example: 11**  
>  Representation: Turtle (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031035 (3)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: text/turtle;profile="http://data.europa.eu/930/"'
> ```


In [12]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'text/turtle;profile="http://data.europa.eu/930/"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://eovoc.spacebel.be>
        a 

<a name='STAC-Collection'></a>     
## STAC Collection  

    
**Example: 12**  
>  Representation: JSON   
> Requirement:  EOVOC-CCAT-IF-033305 (1)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be' -H 'Accept: application/json'
> ```


In [13]:
response = requests.get('https://eovoc.spacebel.be', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -180,
          -90,
          180,
          90
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          null,
          null
        ]
      ]
    }
  },
  "stac_version": "1.0.0-rc.2",
  "license": "various",
  "description": "FedEO Clearinghouse provides interoperable access, following ISO/OGC interface guidelines, to Earth Observation metadata",
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be",
      "type": "application/json",
      "title": "This document"
    },
    {
      "rel": "search",
      "href": "https://eovoc.spacebel.be/api?httpAccept=application/opensearchdescription%2Bxml",
      "type": "application/opensearchdescription+xml",
      "title": "The OpenSearch Description Document"
    },
    {
      "rel": "service-desc",
      "href": "https://eovoc.spacebel.be/api?httpAccept=application/openapi%2Bjson;version=3.0",
      "type": "applicat

>  Representation: JSON   
  Ok  
**Example: 13**  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/json'
> ```


In [14]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -100,
          -50,
          160,
          40
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          "2009-01-27T00:00:00.000Z",
          "2011-08-09T23:59:59.999Z"
        ]
      ]
    }
  },
  "stac_version": "1.0.0-rc.2",
  "keywords": [
    "Multi-mission collection",
    "JRC",
    "Food and Agriculture Organization (FAO)",
    "South East Asia",
    "South America",
    "DE1 663 km;  KO2 685 km; AL1 692 km",
    "DE1 625 km; KO2 15 km; AL1 70 km",
    "VIS (0.40 - 0.75 \u00b5m)",
    "NIR (0.75 - 1.30 \u00b5m)",
    "Sun-synchronous",
    "Very High Resolution - VHR (0 - 5m)",
    "High Resolution - HR (5 - 20 m)",
    "AL1_AV2_2F",
    "DE1_SL6_2F",
    "KO2_MSC_2F",
    "EARTH SCIENCE > AGRICULTURE",
    "EARTH SCIENCE > BIOSPHERE > ECOSYSTEMS > TERRESTRIAL ECOSYSTEMS",
    "EARTH SCIENCE > LAND SURFACE",
    "EARTH SCIENCE > BIOSPHERE > VEGETATION",
    "Agriculture",
    "For

**Example: 14**  
>  Representation: JSON (STAC)   
> Requirement:  (no requirement ?)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/series/eo:platform/ALOS/TropForest' -H 'Accept: application/json'
> ```


In [15]:
response = requests.get('https://eovoc.spacebel.be/series/eo:platform/ALOS/TropForest', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -100,
          -50,
          160,
          40
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          "2009-01-27T00:00:00.000Z",
          "2011-08-09T23:59:59.999Z"
        ]
      ]
    }
  },
  "stac_version": "1.0.0-rc.2",
  "keywords": [
    "Multi-mission collection",
    "JRC",
    "Food and Agriculture Organization (FAO)",
    "South East Asia",
    "South America",
    "DE1 663 km;  KO2 685 km; AL1 692 km",
    "DE1 625 km; KO2 15 km; AL1 70 km",
    "VIS (0.40 - 0.75 \u00b5m)",
    "NIR (0.75 - 1.30 \u00b5m)",
    "Sun-synchronous",
    "Very High Resolution - VHR (0 - 5m)",
    "High Resolution - HR (5 - 20 m)",
    "AL1_AV2_2F",
    "DE1_SL6_2F",
    "KO2_MSC_2F",
    "EARTH SCIENCE > AGRICULTURE",
    "EARTH SCIENCE > BIOSPHERE > ECOSYSTEMS > TERRESTRIAL ECOSYSTEMS",
    "EARTH SCIENCE > LAND SURFACE",
    "EARTH SCIENCE > BIOSPHERE > VEGETATION",
    "Agriculture",
    "For

**Example: 15**  
>  Representation: JSON (STAC)   
> Requirement:  (no requirement ?)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/series/eo:platform/ALOS' -H 'Accept: application/json'
> ```


In [16]:
response = requests.get('https://eovoc.spacebel.be/series/eo:platform/ALOS', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -180,
          -90,
          180,
          90
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          null,
          null
        ]
      ]
    }
  },
  "license": "various",
  "stac_version": "1.0.0-rc.2",
  "description": "EO collections for ALOS platform",
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/series/eo:platform/ALOS",
      "type": "application/json"
    },
    {
      "rel": "root",
      "href": "https://eovoc.spacebel.be",
      "type": "application/json"
    },
    {
      "rel": "parent",
      "href": "https://eovoc.spacebel.be/series/eo:platform",
      "type": "application/json"
    },
    {
      "rel": "child",
      "href": "https://eovoc.spacebel.be/series/eo:platform/ALOS/ALOS_AVNIR-2",
      "type": "application/json",
      "title": "ALOS AVNIR-2 product (0)"
    },
    {
      "rel": "child",
      "href": "https://eovoc.spac

**Example: 16**  
>  Representation: JSON (STAC)   
> Requirement:  (no requirement ?)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/series/eo:platform' -H 'Accept: application/json'
> ```


In [17]:
response = requests.get('https://eovoc.spacebel.be/series/eo:platform', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -180,
          -90,
          180,
          90
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          null,
          null
        ]
      ]
    }
  },
  "stac_version": "1.0.0-rc.2",
  "license": "various",
  "description": "EO platforms",
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/series/eo:platform",
      "type": "application/json"
    },
    {
      "rel": "root",
      "href": "https://eovoc.spacebel.be",
      "type": "application/json"
    },
    {
      "rel": "parent",
      "href": "https://eovoc.spacebel.be",
      "type": "application/json"
    },
    {
      "rel": "child",
      "href": "https://eovoc.spacebel.be/series/eo:platform/ADEOS-I",
      "type": "application/json",
      "title": "ADEOS-I (57)"
    },
    {
      "rel": "child",
      "href": "https://eovoc.spacebel.be/series/eo:platform/ADEOS-II",
      "type": "application/j

**Example: 17**  
>  Representation: JSON (STAC)   
> Requirement:  (no requirement ?)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/earthtopics' -H 'Accept: application/json'
> ```


In [18]:
response = requests.get('https://eovoc.spacebel.be/concepts/earthtopics', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -180,
          -90,
          180,
          90
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          null,
          null
        ]
      ]
    }
  },
  "stac_version": "1.0.0-rc.2",
  "license": "various",
  "description": "Earth Topic",
  "links": [
    {
      "rel": "root",
      "href": "https://eovoc.spacebel.be",
      "type": "application/json"
    },
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/concepts/earthtopics/",
      "type": "application/json"
    },
    {
      "rel": "parent",
      "href": "https://eovoc.spacebel.be",
      "type": "application/json"
    },
    {
      "rel": "child",
      "href": "https://eovoc.spacebel.be/concepts/earthtopics/agriculture",
      "type": "application/json",
      "title": "Agriculture [Earth Topic]"
    },
    {
      "rel": "child",
      "href": "https://eovoc.spacebel.be/concepts/earthtopics/atmosphere",
   

**Example: 18**  
>  Representation: JSON (STAC)   
> Requirement:  (no requirement ?)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/instruments' -H 'Accept: application/json'
> ```


In [19]:
response = requests.get('https://eovoc.spacebel.be/concepts/instruments', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -180,
          -90,
          180,
          90
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          null,
          null
        ]
      ]
    }
  },
  "stac_version": "1.0.0-rc.2",
  "license": "various",
  "description": "Instrument",
  "links": [
    {
      "rel": "root",
      "href": "https://eovoc.spacebel.be",
      "type": "application/json"
    },
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/concepts/instruments/",
      "type": "application/json"
    },
    {
      "rel": "parent",
      "href": "https://eovoc.spacebel.be",
      "type": "application/json"
    },
    {
      "rel": "child",
      "href": "https://eovoc.spacebel.be/concepts/instruments/active-remote-sensing",
      "type": "application/json",
      "title": "Active Remote Sensing [Instrument]"
    },
    {
      "rel": "child",
      "href": "https://eovoc.spacebel.be/concepts/instrument

**Example: 19**  
>  Representation: JSON-LD (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-033305 (2)  
 NOT OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/instruments' -H 'Accept: application/ld+json'
> ```


In [20]:
response = requests.get('https://eovoc.spacebel.be/concepts/instruments', headers={'Accept': 'application/ld+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


JSONDecodeError: Expecting value: line 1 column 1 (char 0)

**Example: 20**  
>  Representation: JSON-LD (schema.org)   
> Requirement:  EOVOC-CCAT-IF-033305 (2)  
 NOT OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/instruments' -H 'Accept: application/ld+json;profile="https://schema.org"'
> ```


In [21]:
response = requests.get('https://eovoc.spacebel.be/concepts/instruments', headers={'Accept': 'application/ld+json;profile="https://schema.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


JSONDecodeError: Expecting value: line 1 column 1 (char 0)

**Example: 21**  
>  Representation: JSON-LD (DCAT)   
> Requirement:  EOVOC-CCAT-IF-033305 (2)  
 NOT TESTED  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/instruments' -H 'Accept: application/ld+json;profile="http://data.europa.eu/930/"'
> ```


In [ ]:
response = requests.get('https://eovoc.spacebel.be/concepts/instruments', headers={'Accept': 'application/ld+json;profile="http://data.europa.eu/930/"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


**Example: 22**  
>  Representation: RDF/XML (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-033305 (3)  
 NOT TESTED  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/instruments' -H 'Accept: application/rdf+xml'
> ```


In [ ]:
response = requests.get('https://eovoc.spacebel.be/concepts/instruments', headers={'Accept': 'application/rdf+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


**Example: 23**  
>  Representation: RDF/XML (schema.org)   
> Requirement:  EOVOC-CCAT-IF-033305 (3)  
 NOT TESTED  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/instruments' -H 'Accept: application/rdf+xml;profile="https://schema.org"'
> ```


In [ ]:
response = requests.get('https://eovoc.spacebel.be/concepts/instruments', headers={'Accept': 'application/rdf+xml;profile="https://schema.org"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


**Example: 24**  
>  Representation: RDF/XML (DCAT)   
> Requirement:  EOVOC-CCAT-IF-033305 (3)  
 NOT TESTED  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/instruments' -H 'Accept: application/rdf+xml;profile="http://data.europa.eu/930/"'
> ```


In [ ]:
response = requests.get('https://eovoc.spacebel.be/concepts/instruments', headers={'Accept': 'application/rdf+xml;profile="http://data.europa.eu/930/"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


**Example: 25**  
>  Representation: Turtle (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-033305 (4)  
 NOT TESTED  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/instruments' -H 'Accept: text/turtle'
> ```


In [ ]:
response = requests.get('https://eovoc.spacebel.be/concepts/instruments', headers={'Accept': 'text/turtle'})
print(response.text)


**Example: 26**  
>  Representation: Turtle (schema.org)   
> Requirement:  EOVOC-CCAT-IF-033305 (4)  
 NOT TESTED  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/instruments' -H 'Accept: text/turtle;profile="https://schema.org"'
> ```


In [ ]:
response = requests.get('https://eovoc.spacebel.be/concepts/instruments', headers={'Accept': 'text/turtle;profile="https://schema.org"'})
print(response.text)


**Example: 27**  
>  Representation: Turtle (DCAT)   
> Requirement:  EOVOC-CCAT-IF-033305 (4)  
 NOT TESTED  
> ```bash
> curl -v 'https://eovoc.spacebel.be/concepts/instruments' -H 'Accept: text/turtle;profile="http://data.europa.eu/930/"'
> ```


In [ ]:
response = requests.get('https://eovoc.spacebel.be/concepts/instruments', headers={'Accept': 'text/turtle;profile="http://data.europa.eu/930/"'})
print(response.text)


<a name='Collections'></a>     
## Collections  
 The `/collections` path is the endpoint for obtaining the list of feature collections.  `series`, `datasets` and `services` are the available feature collections.  
 The feature collection `series` contains the EO collections while the `datasets` feature collection contains the EO granules.  
      
 ![Collections](https://plantuml-server.kkeisuke.dev/png/bP91Jm8n48Nlyoicwq6D0HAFXX1a4Q918S31WvVQ7TbAjoNJRbPZ_Ezs9KWL8Rg7JNRUzsRdJTjrNh0l2mq0GcjR5Uf5cGM0Mogp4YmAbBPOMKF6p_oh9WpiUQHUCjigjTeozhIGoqXAjN2kPpaZtWDiEX-2ne_F97yX85SPeLGiDS4nVdwrsrDojcH9dSv6ShcjWZ0aUpCRtsthNvPhuucVHEo1eAfD6PEuxOD94nGEKoRXQH1U9HCUJNHP06mz8s6oiCU9MFoOQetY6s1upePNyvDJU8-T8QCEWPKrxa_E-4yDLelSDphVcbpK0LR2v_NmBRbL4WIGzHdLm7ev8LsaXpr04XUmcTdAD3lx37WORupw_t1C-uFM_UrePwYzXdd9NjCE7r9soMJXtdu0.png)


    
**Example: 28**  
>  Representation: JSON   
> Requirement:  EOVOC-CCAT-IF-031210 (1)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections' -H 'Accept: application/json'
> ```


In [22]:
response = requests.get('https://eovoc.spacebel.be/collections', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "collections": [
    {
      "extent": {
        "spatial": {
          "bbox": [
            [
              -180,
              -90,
              180,
              90
            ]
          ]
        },
        "temporal": {
          "interval": [
            [
              null,
              null
            ]
          ]
        }
      },
      "stac_version": "1.0.0-rc.2",
      "license": "various",
      "description": "Metadata records representing EO series, datasets and services",
      "links": [
        {
          "rel": "self",
          "href": "https://eovoc.spacebel.be/collections/resources",
          "type": "application/json"
        },
        {
          "rel": "parent",
          "href": "https://eovoc.spacebel.be/collections",
          "type": "application/json"
        },
        {
          "rel": "items",
          "href": "https://eovoc.spacebel.be/collections/resources/items",
          "type": "application/geo+json",
          "title": "Service

**Example: 29**  
>  Representation: JSON-LD (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031210 (2)  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections' -H 'Accept: application/ld+json'
> ```


In [24]:
response = requests.get('https://eovoc.spacebel.be/collections', headers={'Accept': 'application/ld+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dcat:dataset": [
    {
      "@id": "https://eovoc.spacebel.be/collections/resources"
    },
    {
      "@id": "https://eovoc.spacebel.be/collections/series"
    },
    {
      "@id": "https://eovoc.spacebel.be/collections/services"
    },
    {
      "@id": "https://eovoc.spacebel.be/collections/datasets"
    }
  ],
  "@type": "dcat:Dataset",
  "dcat:qualifiedRelation": [
    {
      "dct:relation": "https://eovoc.spacebel.be/collections?httpAccept=application/ld%2Bjson",
      "dct:format": {
        "rdfs:label": "application/ld+json",
        "@type": "dct:MediaType"
      },
      "@type": "dcat:Relationship",
      "dct:title": "Self as JSON-LD (GeoDCAT-AP)",
      "dcat:hadRole": "http://www.iana.org/assignments/relation/self"
    }
  ],
  "@id": "https://eovoc.spacebel.be/collections",
  "@context": {
    "dct": "http://purl.org/dc/terms/",
    "rdfs": "http://www.w3.org/2000/01/rdf-schema#",
    "dcat": "http://www.w3.org/ns/dcat#"
  }
}


**Example: 30**  
>  Representation: JSON-LD (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031210 (2)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections' -H 'Accept: application/ld+json;profile="https://schema.org"'
> ```


In [25]:
response = requests.get('https://eovoc.spacebel.be/collections', headers={'Accept': 'application/ld+json;profile="https://schema.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "@type": "DataCatalog",
  "associatedMedia": [
    {
      "contentUrl": "https://eovoc.spacebel.be/collections",
      "@type": "MediaObject",
      "encodingFormat": "application/json",
      "description": "Self as JSON"
    },
    {
      "contentUrl": "https://eovoc.spacebel.be/collections",
      "@type": "MediaObject",
      "encodingFormat": "application/json",
      "description": "Self as JSON-LD"
    },
    {
      "contentUrl": "https://eovoc.spacebel.be/collections",
      "@type": "MediaObject",
      "encodingFormat": "application/rdf+xml",
      "description": "Self as RDF/XML"
    },
    {
      "contentUrl": "https://eovoc.spacebel.be/collections",
      "@type": "MediaObject",
      "encodingFormat": "text/turtle",
      "description": "Self as Turtle"
    }
  ],
  "@id": "https://eovoc.spacebel.be/collections",
  "@context": "https://schema.org",
  "dataset": [
    {
      "@id": "https://eovoc.spacebel.be/collections/series"
    },
    {
      "@id": "https://e

**Example: 31**  
>  Representation: RDF/XML (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031210 (3)  
  OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections' -H 'Accept: application/rdf+xml'
> ```


In [26]:
response = requests.get('https://eovoc.spacebel.be/collections', headers={'Accept': 'application/rdf+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:Dataset rdf:about="https://eovoc.spacebel.be/collections"

**Example: 32**  
>  Representation: RDF/XML (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031210 (3)  
  OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections' -H 'Accept: application/rdf+xml;profile="https://schema.org"'
> ```


In [27]:
response = requests.get('https://eovoc.spacebel.be/collections', headers={'Accept': 'application/rdf+xml;profile="https://schema.org"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:schema="https://schema.org/" xmlns:wikidata="http://www.wikidata.org/entity/" xmlns:rdfa="http://www.w3.org/ns/rdfa#" xmlns:snomed="http://purl.bioontology.org/ontology/SNOMEDCT/" xmlns:yago="http://yago-knowledge.org/resource/" xmlns:dbpedia="http://dbpedia.org/resource/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:void="http://rdfs.org/ns/void#" xmlns:dcterms="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:dctype="http://purl.org/dc/dcmitype/" xmlns:eli="http://data.europa.eu/eli/ontology#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:bibo="http://purl.org/ontology/bibo/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <schema:DataCatalog rdf:about="https://eovoc.spacebel.be/collections">
      
    
      <s

**Example: 33**  
>  Representation: Turtle (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031210 (4)  
  OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections' -H 'Accept: text/turtle'
> ```


In [28]:
response = requests.get('https://eovoc.spacebel.be/collections', headers={'Accept': 'text/turtle'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://eovoc.spacebel.be/collections

**Example: 34**  
>  Representation: Turtle (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031210 (4)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections' -H 'Accept: text/turtle;profile="https://schema.org"'
> ```


In [29]:
response = requests.get('https://eovoc.spacebel.be/collections', headers={'Accept': 'text/turtle;profile="https://schema.org"'})
print(response.text)


@prefix schema: <https://schema.org/> .
@prefix void:  <http://rdfs.org/ns/void#> .
@prefix eli:   <http://data.europa.eu/eli/ontology#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix snomed: <http://purl.bioontology.org/ontology/SNOMEDCT/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix yago:  <http://yago-knowledge.org/resource/> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix dbpedia: <http://dbpedia.org/resource/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix rdf:   <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dctype: <http://purl.org/dc/dcmitype/> .
@prefix rdfa:  <http://www.w3.org/ns/rdfa#> .
@prefix dcterms: <http://purl.org/dc/terms/> .
@prefix bibo:  <http://purl.org/ontology/bibo/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix wikidata: <http://www.wikidata.org/entity/> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl

**Example: 35**  
>  Representation: JSON-LD (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031212 (1)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections' -H 'Accept: application/ld+json;profile="http://data.europa.eu/930/"'
> ```


In [30]:
response = requests.get('https://eovoc.spacebel.be/collections', headers={'Accept': 'application/ld+json;profile="http://data.europa.eu/930/"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dcat:dataset": [
    {
      "@id": "https://eovoc.spacebel.be/collections/resources"
    },
    {
      "@id": "https://eovoc.spacebel.be/collections/series"
    },
    {
      "@id": "https://eovoc.spacebel.be/collections/services"
    },
    {
      "@id": "https://eovoc.spacebel.be/collections/datasets"
    }
  ],
  "@type": "dcat:Dataset",
  "dcat:qualifiedRelation": [
    {
      "dct:relation": "https://eovoc.spacebel.be/collections?httpAccept=application/ld%2Bjson;profile=\"http://data.europa.eu/930/\"",
      "dct:format": {
        "rdfs:label": "application/ld+json;profile=\"http://data.europa.eu/930/\"",
        "@type": "dct:MediaType"
      },
      "@type": "dcat:Relationship",
      "dct:title": "Self as JSON-LD (GeoDCAT-AP)",
      "dcat:hadRole": "http://www.iana.org/assignments/relation/self"
    }
  ],
  "@id": "https://eovoc.spacebel.be/collections",
  "@context": {
    "dct": "http://purl.org/dc/terms/",
    "rdfs": "http://www.w3.org/2000/01/rdf-schema#",
  

**Example: 36**  
>  Representation: RDF/XML (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031212 (2)  
  OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections' -H 'Accept: application/rdf+xml;profile="http://data.europa.eu/930/"'
> ```


In [31]:
response = requests.get('https://eovoc.spacebel.be/collections', headers={'Accept': 'application/rdf+xml;profile="http://data.europa.eu/930/"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:Dataset rdf:about="https://eovoc.spacebel.be/collections"

**Example: 37**  
>  Representation: Turtle (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031212 (3)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections' -H 'Accept: text/turtle;profile="http://data.europa.eu/930/"'
> ```


In [32]:
response = requests.get('https://eovoc.spacebel.be/collections', headers={'Accept': 'text/turtle;profile="http://data.europa.eu/930/"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://eovoc.spacebel.be/collections

<a name='Collection'></a>     
## Collection  
 The `/collections/{collection-id}` path is the endpoint for obtaining a feature collection description.  `series`, `datasets` and `services` are the available feature collections.  
 The feature collection `series` contains the EO collections while the `datasets` feature collection contains the EO granules.  
      
 ![Collection](https://plantuml-server.kkeisuke.dev/png/VPB1Jy8m6CNl_IiQFAWnWmYU35cG8KI3Oe231o-r-sILhYLjbsa8_xijE6YJwWvDzhxVUtdzqe4sH9cgv0WXmhciI_R5n0eXlMPYGnGfCPNbHWeGPc6-EM3BThtfdLAopYIN2WyveMjlb76YzL2g7DGVG9Fy7pHx_mGQ8L31Si2KASe1dUFzNxy_1oqhHI5Dcv4kP6q74v2FYzdpIJzQ7eG1zK5y3x9JriYuvSU-YQo5YSQP0c9WR8zA0JvxuLLfRIUJhSfjRoQ53ciTMBn5s7vNa_lbnINQnPsXqVCbzCWaB4T144BKxTsrFbpODZxI--hq-f3Yw81DfgCOtlqj6_3pqRZp-ZIDyJt71_2oKeP3ZBrfM7zVYMAhmYIflufRbxCXfd0fdMsmW5tBz-DsBclHJjqzutetBlVYyerTwG14RX_-3m00.png)


    
**Example: 38**  
>  Representation: JSON   
> Requirement:  EOVOC-CCAT-IF-031310 (1)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: application/json'
> ```


In [33]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -180,
          -90,
          180,
          90
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          null,
          null
        ]
      ]
    }
  },
  "stac_version": "1.0.0-rc.2",
  "license": "various",
  "description": "Metadata records representing EO series (a.k.a. EO collections).",
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/collections/series",
      "type": "application/json"
    },
    {
      "rel": "parent",
      "href": "https://eovoc.spacebel.be/collections",
      "type": "application/json"
    },
    {
      "rel": "items",
      "href": "https://eovoc.spacebel.be/collections/series/items",
      "type": "application/geo+json",
      "title": "Series"
    },
    {
      "rel": "describedBy",
      "href": "http://schemas.opengis.net/eoc-geojson/1.0/eoc-geojson-schema.json",
      "type": "application/schema+json",
      "title": "JS

**Example: 39**  
>  Representation: JSON-LD (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031310 (2)  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: application/ld+json'
> ```


In [34]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'application/ld+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dcat:distribution": [
    {
      "dcat:mediaType": {
        "rdfs:label": "application/ld+json",
        "@type": "dct:MediaType"
      },
      "dcat:accessURL": "https://eovoc.spacebel.be/collections/series/items?httpAccept=application/ld%2Bjson",
      "@type": "dcat:Distribution",
      "dct:title": "Series as JSON-LD (GeoDCAT-AP)"
    }
  ],
  "dct:spatial": {
    "@type": "dct:Location",
    "dcat:bbox": "POLYGON((-180 -90, 180 90))"
  },
  "@type": "dcat:Dataset",
  "dcat:qualifiedRelation": [
    {
      "dct:relation": "https://eovoc.spacebel.be/collections/series?httpAccept=application/ld%2Bjson",
      "dct:format": {
        "rdfs:label": "application/ld+json",
        "@type": "dct:MediaType"
      },
      "@type": "dcat:Relationship",
      "dct:title": "Self as JSON-LD (GeoDCAT-AP)",
      "dcat:hadRole": "http://www.iana.org/assignments/relation/self"
    },
    {
      "dct:relation": "https://eovoc.spacebel.be/collections?httpAccept=application/ld%2Bjson",
   

**Example: 40**  
>  Representation: JSON-LD (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031310 (2)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: application/ld+json;profile="https://schema.org"'
> ```


In [35]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'application/ld+json;profile="https://schema.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "temporalCoverage": "../..",
  "@type": "Dataset",
  "name": "EO Series",
  "description": "Metadata records representing EO series (a.k.a. EO collections).",
  "@id": "https://eovoc.spacebel.be/collections/series",
  "spatial": [
    {
      "geo": {
        "@type": "GeoShape",
        "box": "-180,-90 180,90"
      },
      "@type": "Place"
    }
  ],
  "distribution": [
    {
      "contentUrl": "https://eovoc.spacebel.be/collections/series",
      "@type": "DataDownload",
      "encodingFormat": "application/json",
      "description": "Self as JSON"
    },
    {
      "contentUrl": "https://eovoc.spacebel.be/collections/series",
      "@type": "DataDownload",
      "encodingFormat": "application/json",
      "description": "Self as JSON-LD"
    },
    {
      "contentUrl": "https://eovoc.spacebel.be/collections/series",
      "@type": "DataDownload",
      "encodingFormat": "application/rdf+xml",
      "description": "Self as RDF/XML"
    },
    {
      "contentUrl": "https:/

**Example: 41**  
>  Representation: RDF/XML (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031310 (3)  
  OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: application/rdf+xml'
> ```


In [36]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'application/rdf+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:Dataset rdf:about="https://eovoc.spacebel.be/collections/

**Example: 42**  
>  Representation: RDF/XML (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031310 (3)  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: application/rdf+xml;profile="https://schema.org"'
> ```


In [37]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'application/rdf+xml;profile="https://schema.org"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:schema="https://schema.org/" xmlns:wikidata="http://www.wikidata.org/entity/" xmlns:rdfa="http://www.w3.org/ns/rdfa#" xmlns:snomed="http://purl.bioontology.org/ontology/SNOMEDCT/" xmlns:yago="http://yago-knowledge.org/resource/" xmlns:dbpedia="http://dbpedia.org/resource/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:void="http://rdfs.org/ns/void#" xmlns:dcterms="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:dctype="http://purl.org/dc/dcmitype/" xmlns:eli="http://data.europa.eu/eli/ontology#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:bibo="http://purl.org/ontology/bibo/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <schema:Dataset rdf:about="https://eovoc.spacebel.be/collections/series">
      
    
     

**Example: 43**  
>  Representation: Turtle (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031310 (4)  
  NOT OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: text/turtle'
> ```


In [38]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'text/turtle'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://eovoc.spacebel.be/collections

**Example: 44**  
>  Representation: Turtle (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031310 (4)  
  NOT OK - too many unused namespaces included.  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: text/turtle;profile="https://schema.org"'
> ```


In [39]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'text/turtle;profile="https://schema.org"'})
print(response.text)


@prefix schema: <https://schema.org/> .
@prefix void:  <http://rdfs.org/ns/void#> .
@prefix eli:   <http://data.europa.eu/eli/ontology#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix snomed: <http://purl.bioontology.org/ontology/SNOMEDCT/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix yago:  <http://yago-knowledge.org/resource/> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix dbpedia: <http://dbpedia.org/resource/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix rdf:   <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dctype: <http://purl.org/dc/dcmitype/> .
@prefix rdfa:  <http://www.w3.org/ns/rdfa#> .
@prefix dcterms: <http://purl.org/dc/terms/> .
@prefix bibo:  <http://purl.org/ontology/bibo/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix wikidata: <http://www.wikidata.org/entity/> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl

**Example: 45**  
>  Representation: JSON-LD (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031312 (1)  
  OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: application/ld+json;profile="http://data.europa.eu/930/"'
> ```


In [40]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'application/ld+json;profile="http://data.europa.eu/930/"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dcat:distribution": [
    {
      "dcat:mediaType": {
        "rdfs:label": "application/ld+json;profile=\"http://data.europa.eu/930/\"",
        "@type": "dct:MediaType"
      },
      "dcat:accessURL": "https://eovoc.spacebel.be/collections/series/items?httpAccept=application/ld%2Bjson;profile=\"http://data.europa.eu/930/\"",
      "@type": "dcat:Distribution",
      "dct:title": "Series as JSON-LD (GeoDCAT-AP)"
    }
  ],
  "dct:spatial": {
    "@type": "dct:Location",
    "dcat:bbox": "POLYGON((-180 -90, 180 90))"
  },
  "@type": "dcat:Dataset",
  "dcat:qualifiedRelation": [
    {
      "dct:relation": "https://eovoc.spacebel.be/collections/series?httpAccept=application/ld%2Bjson;profile=\"http://data.europa.eu/930/\"",
      "dct:format": {
        "rdfs:label": "application/ld+json;profile=\"http://data.europa.eu/930/\"",
        "@type": "dct:MediaType"
      },
      "@type": "dcat:Relationship",
      "dct:title": "Self as JSON-LD (GeoDCAT-AP)",
      "dcat:hadRole": "htt

**Example: 46**  
>  Representation: RDF/XML (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031312 (2)  
  OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: application/rdf+xml;profile="http://data.europa.eu/930/"'
> ```


In [41]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'application/rdf+xml;profile="http://data.europa.eu/930/"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:Dataset rdf:about="https://eovoc.spacebel.be/collections/

**Example: 47**  
>  Representation: Turtle (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031312 (3)  
  NOT OK - duplicate namespace dct, dcterms  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: text/turtle;profile="http://data.europa.eu/930/"'
> ```


In [42]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'text/turtle;profile="http://data.europa.eu/930/"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://eovoc.spacebel.be/collections

**Example: 48**  
>  Representation: text/html   
> Requirement:  EOVOC-CCAT-IF-035430  
>  Kind: EO Series  
  NOT OK - wrong media type (no HTML returned).  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series' -H 'Accept: text/html'
> ```


In [43]:
response = requests.get('https://eovoc.spacebel.be/collections/series', headers={'Accept': 'text/html'})
print(response.text)


{
  "extent": {
    "spatial": {"bbox": [[
      -180,
      -90,
      180,
      90
    ]]},
    "temporal": {"interval": [[
      null,
      null
    ]]}
  },
  "stac_version": "1.0.0-rc.2",
  "license": "various",
  "description": "Metadata records representing EO series (a.k.a. EO collections).",
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/collections/series",
      "type": "application/json"
    },
    {
      "rel": "parent",
      "href": "https://eovoc.spacebel.be/collections",
      "type": "application/json"
    },
    {
      "rel": "items",
      "href": "https://eovoc.spacebel.be/collections/series/items",
      "type": "application/geo+json",
      "title": "Series"
    },
    {
      "rel": "describedBy",
      "href": "http://schemas.opengis.net/eoc-geojson/1.0/eoc-geojson-schema.json",
      "type": "application/schema+json",
      "title": "JSON schema for items belonging to this collection"
    }
  ],
  "id": "series",
  "title"

<a name='APIDefinition'></a>     
## APIDefinition  
 The `APIDefinition` is available at the `/api` path.  It is available in multiple representations
 according to multiple profiles.   OpenSearch clients can obtain the OpenSearch Description Document (OSDD) and more 
 sophisticated clients may prefer using the OpenAPI Definition.
      
 ![APIDefinition](https://plantuml-server.kkeisuke.dev/png/ZPDHIyCm58NVyoj2VL2HJV1HHjdMpJ6PRZWV9kpbcjwjSMbIafHDnFzkugZjfAtseT2SyvtSUw1zOq7RF1M44112xLD-u79BYDbncO66b3ALPagYj4lxBf0wxqr57MYjzf4IIjEX0BQhI940OuPAnwWR34Locsd--eQina4I7YDbN3E1v9n-V_LwJsXKhXc6OI6PHEsTC45rlvm_bkS_o5HQr1keCiIfl3YcGJLsBQE0Wg6HHh1uvrwvHdgs47bAICdCGCQknmLiVqrrjD8FGjrpDHa_NroIpoevM4n7kE6IMwxaALj1Iv8GvdlsKnuNNCjvXjB5q95YUUhg3MZfUHaypDezNbaYQ9RG4HgcUUOd2TmeAu-MKQjZqlYG2U2ozhPYeXeFgLRKqNoRs4xuQ_jRdv61JNp6DMJSSy699w3TMErbD_oZW1QgfP96gg6ajckQwlhFGdNzzL76xcVy0W00.png)

   
**Example: 49**  
>  Representation: OSDD   
> Requirement:  None.  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/api' -H 'Accept: application/opensearchdescription+xml'
> ```


In [44]:
response = requests.get('https://eovoc.spacebel.be/api', headers={'Accept': 'application/opensearchdescription+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<os:OpenSearchDescription xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:eo="http://a9.com/-/opensearch/extensions/eo/1.0/" xmlns:geo="http://a9.com/-/opensearch/extensions/geo/1.0/" xmlns:param="http://a9.com/-/spec/opensearch/extensions/parameters/1.0/" xmlns:referrer="http://a9.com/-/opensearch/extensions/referrer/1.0/" xmlns:semantic="http://a9.com/-/opensearch/extensions/semantic/1.0/" xmlns:sru="http://a9.com/-/opensearch/extensions/sru/2.0/" xmlns:time="http://a9.com/-/opensearch/extensions/time/1.0/">
   
    
   <os:ShortName>FedEO</os:ShortName>
   
    
   <os:Description>Provides interoperable access, following ISO/OGC interface guidelines, to Earth Observation metadata.</os:Description>
   
    
   <os:Tags>FEDEO, ESA, Earth Observation, Digital Repository, HMA, HMA-S, HMA-SE, CEOS-OS-BP-V1.1/L1.</os:Tags>
   
    
   <os:Url rel="self" template="https://eovoc.spacebel.be/api?null" type="application/

**Example: 50**  
>  Representation: OpenAPI   
> Requirement:  None.  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/api' -H 'Accept: application/openapi+json;version=3.0'
> ```


In [45]:
response = requests.get('https://eovoc.spacebel.be/api', headers={'Accept': 'application/openapi+json;version=3.0'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "x-@context": {
    "geo": "http://a9.com/-/opensearch/extensions/geo/1.0/",
    "semantic": "http://a9.com/-/opensearch/extensions/semantic/1.0/",
    "referrer": "http://a9.com/-/opensearch/extensions/referrer/1.0/",
    "os": "http://a9.com/-/spec/opensearch/1.1/",
    "sru": "http://a9.com/-/opensearch/extensions/sru/2.0/",
    "eo": "http://a9.com/-/opensearch/extensions/eo/1.0/",
    "time": "http://a9.com/-/opensearch/extensions/time/1.0/",
    "dc": "http://purl.org/dc/elements/1.1/"
  },
  "components": {
    "schemas": {
      "MultiPoint": {
        "additionalProperties": false,
        "title": "MultiPoint",
        "type": "object",
        "properties": {
          "coordinates": {
            "minItems": 1,
            "description": "Array of positions",
            "title": "coordinates",
            "type": "array",
            "items": {
              "minItems": 2,
              "maxItems": 2,
              "description": "One position",
              "type": "

<a name='Features'></a>     
## Features  
 The `/collections/{collection}/items` path is the endpoint for performing searches in one of the available feature collections.
 All search parameters defined by the OpenSearch OSDD and/or the OpenAPI definition of the FedEO Catalog API can be used.  
      
 ![Features](https://plantuml-server.kkeisuke.dev/png/XPDTJy8m58Rl-okQUO76096l2xCiV0bgK0XmuGKtTJkmIjUIjiiqXl_kEXaReSgvwjxtEU_fHzPLcaWTHmoP8eo99AAVb6yGKblATqII2FiYsWaEN2_q5mESqerBTk7sf1J9G30XSPyHVrko1emerHSo0Fa7a2V_1qtVFy2t42Ya0M2VIfy1gk3iotNde4GiVV2ymbAXI59h3E9vCNsrE3qjelhRowHi7VAUk0Qv9kN0j6YkfaTWBDqU5Vnq-DMCnH7-HXZZs_73yle6xK_wHa1qB45TwggOvMowE2IKnbKbtOIwwXLHzzXntHtHeUUjU9rgY9IJlRjl7iAOnojOyRpBmKJXzLqwT5ycizieKndMC7ipu94pSTN9qCAspjZvS5ItvpP_nn_9PImr0mlOFWjzN5eJEpc8a5DOjK0alEQPyrhbXbLjMjMMLMrRrGuwgIxm8FsDVW00.png)


**Example: 51**  
>  Representation: GeojSON   
> Requirement:  None.  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items' -H 'Accept: application/geo+json'
> ```


In [46]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items', headers={'Accept': 'application/geo+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "facetedResults": {
    "datasource": [
      {
        "displayLabel": "FedEO Clearinghouse",
        "baseURL": "https://eovoc.spacebel.be",
        "description": "FedEO Clearinghouse",
        "facets": [
          {
            "displayLabel": "Platform",
            "terms": [
              {
                "actualTerm": "Envisat",
                "count": 4155409
              },
              {
                "actualTerm": "ERS",
                "count": 2374458
              },
              {
                "actualTerm": "SMOS",
                "count": 666734
              },
              {
                "actualTerm": "JERS",
                "count": 219199
              },
              {
                "actualTerm": "OceanSat",
                "count": 83230
              },
              {
                "actualTerm": "SPOT",
                "count": 32680
              },
              {
                "actualTerm": "PROBA",
                "count": 25998
  

Display the features on the map.


In [47]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 53**  
>  Representation: GeojSON   
> Requirement:  None.  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: application/geo+json'
> ```


In [48]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'application/geo+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "facetedResults": {
    "datasource": [
      {
        "displayLabel": "FedEO Clearinghouse",
        "baseURL": "https://eovoc.spacebel.be",
        "description": "FedEO Clearinghouse",
        "facets": [
          {
            "displayLabel": "Platform",
            "terms": [
              {
                "actualTerm": "GCOM-C1",
                "count": 610
              },
              {
                "actualTerm": "Envisat",
                "count": 231
              },
              {
                "actualTerm": "AQUA",
                "count": 227
              },
              {
                "actualTerm": "Metop-A",
                "count": 201
              },
              {
                "actualTerm": "ADEOS-II",
                "count": 190
              },
              {
                "actualTerm": "NOAA-16",
                "count": 138
              },
              {
                "actualTerm": "NOAA-18",
                "count": 138
          

Display the features on the map.


In [49]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 55**  
>  Representation: JSON-LD (default)   
> Requirement:  EOVOC-CCAT-IF-035020  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: application/ld+json'
> ```


In [50]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'application/ld+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:date": "2022-03-24T08:48:29Z",
  "@type": [
    "ldp:Resource",
    "ldp:Page"
  ],
  "os:Query": {
    "dc:type": "collection",
    "os:count": "10",
    "os:startIndex": "1"
  },
  "os:itemsPerPage": 10,
  "@context": {
    "void": "http://rdfs.org/ns/void#",
    "adms": "http://www.w3.org/ns/adms#",
    "os": "http://a9.com/-/spec/opensearch/1.1/",
    "gsp": "http://www.opengis.net/ont/geosparql#",
    "owl": "http://www.w3.org/2002/07/owl#",
    "xsd": "http://www.w3.org/2001/XMLSchema#",
    "skos": "http://www.w3.org/2004/02/skos/core#",
    "rdfs": "http://www.w3.org/2000/01/rdf-schema#",
    "eo": "http://a9.com/-/opensearch/extensions/eo/1.0/",
    "vcard": "http://www.w3.org/2006/vcard/ns#",
    "dct": "http://purl.org/dc/terms/",
    "ldp": "http://www.w3.org/ns/ldp#",
    "iana": "http://www.iana.org/assignments/relation/",
    "owc": "http://www.opengis.net/ont/owc/1.0/",
    "dcat": "http://www.w3.org/ns/dcat#",
    "locn": "http://www.w3.org/ns/locn#",
    "pro

**Example: 56**  
>  Representation: JSON-LD (OGC)   
> Requirement:  EOVOC-CCAT-IF-031528  
 OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: application/ld+json;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [51]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'application/ld+json;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:modified": "2022-03-24T08:48:29Z",
  "dct:rights": "Copyright 2016-2020, European Space Agency",
  "@type": "gj:FeatureCollection",
  "owc:links": {
    "iana:profiles": [
      {
        "@id": "http://www.opengis.net/spec/owc-geojson/1.0/req/core"
      },
      {
        "@id": "http://www.opengis.net/spec/os-geojson/1.0/req/core"
      }
    ],
    "iana:first": {
      "atom:type": "application/ld+json;profile=\"http://www.opengis.net/spec/os-geojson/1.0\"",
      "@id": "https://eovoc.spacebel.be/collections/series/items?startRecord=1",
      "dct:title": "first results"
    },
    "iana:next": {
      "atom:type": "application/ld+json;profile=\"http://www.opengis.net/spec/os-geojson/1.0\"",
      "@id": "https://eovoc.spacebel.be/collections/series/items?startRecord=11",
      "dct:title": "next results"
    },
    "iana:alternate": [
      {
        "atom:type": "application/atom+xml",
        "@id": "https://eovoc.spacebel.be/collections/series/items?httpAccept=applic

**Example: 57**  
>  Representation: JSON-LD (DCAT)   
> Requirement:  EOVOC-CCAT-IF-035022  
 OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: application/ld+json;profile="http://data.europa.eu/930/"'
> ```


In [52]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'application/ld+json;profile="http://data.europa.eu/930/"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:date": "2022-03-24T08:48:30Z",
  "@type": [
    "ldp:Resource",
    "ldp:Page"
  ],
  "os:Query": {
    "dc:type": "collection",
    "os:count": "10",
    "os:startIndex": "1"
  },
  "os:itemsPerPage": 10,
  "@context": {
    "void": "http://rdfs.org/ns/void#",
    "adms": "http://www.w3.org/ns/adms#",
    "os": "http://a9.com/-/spec/opensearch/1.1/",
    "gsp": "http://www.opengis.net/ont/geosparql#",
    "owl": "http://www.w3.org/2002/07/owl#",
    "xsd": "http://www.w3.org/2001/XMLSchema#",
    "skos": "http://www.w3.org/2004/02/skos/core#",
    "rdfs": "http://www.w3.org/2000/01/rdf-schema#",
    "eo": "http://a9.com/-/opensearch/extensions/eo/1.0/",
    "vcard": "http://www.w3.org/2006/vcard/ns#",
    "dct": "http://purl.org/dc/terms/",
    "ldp": "http://www.w3.org/ns/ldp#",
    "iana": "http://www.iana.org/assignments/relation/",
    "owc": "http://www.opengis.net/ont/owc/1.0/",
    "dcat": "http://www.w3.org/ns/dcat#",
    "locn": "http://www.w3.org/ns/locn#",
    "pro

**Example: 58**  
>  Representation: JSON-LD (schema.org)   
> Requirement:  EOVOC-CCAT-IF-035024  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: application/ld+json;profile="https://schema.org"'
> ```


In [53]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'application/ld+json;profile="https://schema.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "hasPart": [
    {
      "keywords": [
        {
          "@type": "DefinedTerm",
          "name": "Land Surface",
          "@id": "https://earth.esa.int/concept/land-surface",
          "inDefinedTermSet": "https://earth.esa.int/concepts/concept_scheme/earth-topics"
        },
        {
          "@type": "DefinedTerm",
          "name": "Snow and Ice",
          "@id": "https://earth.esa.int/concept/snow-ice",
          "inDefinedTermSet": "https://earth.esa.int/concepts/concept_scheme/earth-topics"
        },
        {
          "@type": "DefinedTerm",
          "name": "Vegetation",
          "@id": "https://earth.esa.int/concept/vegetation",
          "inDefinedTermSet": "https://earth.esa.int/concepts/concept_scheme/earth-topics"
        },
        {
          "@type": "DefinedTerm",
          "name": "Soils",
          "@id": "https://earth.esa.int/concept/soils",
          "inDefinedTermSet": "https://earth.esa.int/concepts/concept_scheme/earth-topics"
        },
       

**Example: 59**  
>  Representation: RDF/XML (OGC)   
> Requirement:  EOVOC-CCAT-IF-035026  
  TBD    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: application/rdf+xml;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [54]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'application/rdf+xml;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:geo="http://a9.com/-/opensearch/extensions/geo/1.0/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:eop="http://www.opengis.net/ont/eo-geojson/1.0/" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#" xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:eo="http://a9.com/-/opensearch/extensions/eo/1.0/" xmlns:sru="http://a9.com/-/opensearch/extensions/sru/2.0/" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:gj="https://purl.org/geojson/vocab#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:time="http://a9.com/-/opensearch/extensions/time/1.0/" xmlns:owl="http://www.w3.org/2002/07/owl

**Example: 60**  
>  Representation: RDF/XML (DCAT)   
> Requirement:  EOVOC-CCAT-IF-035028  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: application/rdf+xml;profile="http://data.europa.eu/930/"'
> ```


In [55]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'application/rdf+xml;profile="http://data.europa.eu/930/"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <ldp:Resource rdf:about="https://eovoc.spacebel.be/collections/

**Example: 61**  
>  Representation: RDF/XML (schema.org)   
> Requirement:  EOVOC-CCAT-IF-035030  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: application/rdf+xml;profile="https://schema.org"'
> ```


In [56]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'application/rdf+xml;profile="https://schema.org"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:schema="https://schema.org/" xmlns:wikidata="http://www.wikidata.org/entity/" xmlns:rdfa="http://www.w3.org/ns/rdfa#" xmlns:snomed="http://purl.bioontology.org/ontology/SNOMEDCT/" xmlns:yago="http://yago-knowledge.org/resource/" xmlns:dbpedia="http://dbpedia.org/resource/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:void="http://rdfs.org/ns/void#" xmlns:dcterms="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:dctype="http://purl.org/dc/dcmitype/" xmlns:eli="http://data.europa.eu/eli/ontology#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:bibo="http://purl.org/ontology/bibo/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <schema:Collection rdf:about="https://eovoc.spacebel.be/collections/series/items">
      
 

**Example: 62**  
>  Representation: Turtle (OGC)   
> Requirement:  EOVOC-CCAT-IF-035032  
  OK     
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: text/turtle;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [57]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'text/turtle;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix gj:    <https://purl.org/geojson/vocab#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix eop:   <http://www.opengis.net/ont/eo-geojson/1.0/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix eo:    <http://a9.com/-/opensearch/extensions/eo/1.0/> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix geo:   <http://a9.com/-/opensearch/extensions/geo/1.0/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix sru:   <http://a9.com/-/opensearch/extensions/sru/2.0/> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix time:  <http://a9.com/-/opensearch/extensions/time

**Example: 63**  
>  Representation: Turtle (DCAT)   
> Requirement:  EOVOC-CCAT-IF-035034  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: text/turtle;profile="http://data.europa.eu/930/"'
> ```


In [58]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'text/turtle;profile="http://data.europa.eu/930/"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://gcmd.earthdata.nasa.gov/kms/c

**Example: 64**  
>  Representation: Turtle (schema.org)   
> Requirement:  EOVOC-CCAT-IF-035036  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: text/turtle;profile="https://schema.org"'
> ```


In [59]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'text/turtle;profile="https://schema.org"'})
print(response.text)


@prefix schema: <https://schema.org/> .
@prefix void:  <http://rdfs.org/ns/void#> .
@prefix eli:   <http://data.europa.eu/eli/ontology#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix snomed: <http://purl.bioontology.org/ontology/SNOMEDCT/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix yago:  <http://yago-knowledge.org/resource/> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix dbpedia: <http://dbpedia.org/resource/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix rdf:   <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dctype: <http://purl.org/dc/dcmitype/> .
@prefix rdfa:  <http://www.w3.org/ns/rdfa#> .
@prefix dcterms: <http://purl.org/dc/terms/> .
@prefix bibo:  <http://purl.org/ontology/bibo/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix wikidata: <http://www.wikidata.org/entity/> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl

**Example: 65**  
>  Representation: text/html   
> Requirement:  EOVOC-CCAT-IF-035430  
>  Kind: EO Series  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items' -H 'Accept: text/html'
> ```


In [60]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items', headers={'Accept': 'text/html'})
print(response.text)


<html>
	<head>
                <title>FedEO Clearinghouse - Search Response</title>
                <meta name="viewport" content="width=device-width, initial-scale=1.0">
		<meta content="text/html; charset=UTF-8" http-equiv="content-type"/>
		<link rel="stylesheet" type="text/css" href="https://eovoc.spacebel.be/css/default.css"/>
                		
	</head>
	<body>
		<table width="100%">
			<tr>
				<td>
					<table class="bannerTable">
						<tr>
							<td class="bannerLeft">								                                                  
							</td>
							<td class="bannerRight">
								<b>fedeo</b>
								<br/>
								Federated EO missions support environment
							</td>
						</tr>
					</table>				
				</td>				
			</tr>
		</table>
		<div class="container"><div class="title"><h1>Search Response &nbsp;&nbsp;&nbsp;<small><a href='https://eovoc.spacebel.be/collections/series/items'>View Full Response</a></small><small class="paging"><a href='https://eovoc.spacebel.be/collections/s

<a name='Feature'></a>     
## Feature  
 The `/collections/{collection-id}/items/{id}` path allows for obtaining a `Feature` in a specific representation.  
      
 ![Features](https://plantuml-server.kkeisuke.dev/png/ZPDHJy8m58NV-okQ-Q3632883uOio1YeGI4m4nzugLjXawubRPTf2F_TTh0nicfyMRfpltFkxLtM5n9ncIO40808OLaIVyLq3O3On7IBE4fWm98jevZAXVmc62gsLQa-SCuobn76uO2WO5CfkGG9CM0ynFmNe4Z-2vf-VEB0G80e3Z4COXuG32vX_jRhpR5WAG-munGb4R5C5SQOFI-choUzj3nHYVaALJr0LUD2XbOrTabT2o81NOwHn2FrI3c65pEI9ifsCXqhudocd8Cx026y6Nl-rRLgf8wpwKAVzuQ0V_c7tiJplJBjxHWMw0-WnoyllwJ7sFmEgriLfRWJ-FuoEODoggKRdkNfC7iohADtDNG-73MDgUr3xnBqKou9hdETMkIZRyhh5bovUPl7wqZQJhdAU-tU8XbfTtEtEiXs7EujgBPWbO6Da6MquUW5cTIMIMoRn3kJs369NJK0w6CQgl_h1m00.png)

 The representations available depend on the type of resource: i.e. 
 EO Collection, EO Service or EO Granule.


<a name='Feature--EO-Collection'></a>     
### Feature (EO Collection)  
 The representations available for an EO Collection include but are not limited to:
 * ISO19139
 * ISO19139-2
 * OGC 17-084r1
 * DIF-10
 * STAC
 * GeoDCAT-AP
 * Schema.org
 * HTML

>    
**Example: 66**  
>  Representation: ISO19139   
> Requirement:  None.  
>  Kind: EO Collection  
 OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/vnd.iso.19139+xml'
> ```


In [61]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/vnd.iso.19139+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<gmd:MD_Metadata xmlns:gmd="http://www.isotc211.org/2005/gmd" xmlns:gco="http://www.isotc211.org/2005/gco" xmlns:gmi="http://www.isotc211.org/2005/gmi" xmlns:gml="http://www.opengis.net/gml" xmlns:gmx="http://www.isotc211.org/2005/gmx" xmlns:srv="http://www.isotc211.org/2005/srv" xmlns:xlink="http://www.w3.org/1999/xlink" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://www.isotc211.org/2005/gmd http://www.isotc211.org/2005/gmd/gmd.xsd">
   

   <gmd:fileIdentifier>
        
      <!-- Metadata Identification Identifier  (MI_I)-->
        
      <gco:CharacterString>TropForest</gco:CharacterString>
       
   </gmd:fileIdentifier>
   

   <gmd:language>
        
      <gmd:LanguageCode codeList="http://standards.iso.org/ittf/PubliclyAvailableStandards/ISO_19139_Schemas/resources/codelist/gmxCodelists.xml#LanguageCode" codeListValue="eng">eng</gmd:LanguageCode>
       
   </gmd:language>
   

   <gmd:hierarchyLevel>
        
      <

>    
**Example: 67**  
>  Representation: ISO19139-2   
> Requirement:  None  
>  Kind: EO Collection  
 OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/vnd.iso.19139-2+xml'
> ```


In [62]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/vnd.iso.19139-2+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<gmi:MI_Metadata xmlns:gmi="http://www.isotc211.org/2005/gmi" xmlns:gco="http://www.isotc211.org/2005/gco" xmlns:gmx="http://www.isotc211.org/2005/gmx" xmlns:xlink="http://www.w3.org/1999/xlink">
    
   <gmd:fileIdentifier xmlns:gmd="http://www.isotc211.org/2005/gmd">
        
      <!-- Metadata Identification Identifier  (MI_I)-->
        
      <gco:CharacterString>TropForest</gco:CharacterString>
       
   </gmd:fileIdentifier>
    
   <gmd:language xmlns:gmd="http://www.isotc211.org/2005/gmd">
        
      <gmd:LanguageCode codeList="http://standards.iso.org/ittf/PubliclyAvailableStandards/ISO_19139_Schemas/resources/codelist/gmxCodelists.xml#LanguageCode" codeListValue="eng">eng</gmd:LanguageCode>
       
   </gmd:language>
    
   <gmd:hierarchyLevel xmlns:gmd="http://www.isotc211.org/2005/gmd">
        
      <gmd:MD_ScopeCode codeList="http://standards.iso.org/ittf/PubliclyAvailableStandards/ISO_19139_Schemas/resources/codelist/gmxCodelists.xml#MD_Sc

>    
**Example: 68**  
>  Representation: DIF-10   
> Requirement:  None  
>  Kind: EO Collection  
 OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/dif10+xml'
> ```


In [63]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/dif10+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<DIF xmlns="http://gcmd.gsfc.nasa.gov/Aboutus/xml/dif/" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://gcmd.gsfc.nasa.gov/Aboutus/xml/dif/ https://gcmd.gsfc.nasa.gov/Aboutus/xml/dif/dif_v10.2.xsd">
   

   <Entry_ID>
      

      <Short_Name>TropForest</Short_Name>
      

      <Version>NA</Version>
      

   </Entry_ID>
   

   <Entry_Title>TropForest- ALOS, Deimos-1 &amp; KOMPSAT-2 optical coverages over tropical forests</Entry_Title>
   

   <Science_Keywords>
      

      <Category>EARTH SCIENCE</Category>
      

      <Topic>BIOSPHERE</Topic>
      

      <Term>ECOSYSTEMS</Term>
      

      <Variable_Level_1>TERRESTRIAL ECOSYSTEMS</Variable_Level_1>
      

   </Science_Keywords>
   

   <Science_Keywords>
      

      <Category>EARTH SCIENCE</Category>
      

      <Topic>BIOSPHERE</Topic>
      

      <Term>VEGETATION</Term>
      

   </Science_Keywords>
   

   <ISO_Topic_Category>IMAGERY/BASE MAPS/EARTH COVER

**Example: 69**  
>  Representation: GeoJSON (default=OGC 17-069r3)   
> Requirement:  ERGO-CCAT-IF-031514  
>  Kind: EO Collection  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/geo+json'
> ```


In [64]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/geo+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": {
    "coordinates": [
      [
        [
          -100,
          -50
        ],
        [
          160,
          -50
        ],
        [
          160,
          40
        ],
        [
          -100,
          40
        ],
        [
          -100,
          -50
        ]
      ]
    ],
    "type": "Polygon"
  },
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/collections/series/items/TropForest",
      "type": "application/geo+json"
    },
    {
      "rel": "collection",
      "href": "https://eovoc.spacebel.be/collections/series",
      "type": "application/json",
      "title": "the collection document"
    },
    {
      "rel": "search",
      "href": "https://eovoc.spacebel.be/collections/series/items/TropForest/api",
      "type": "application/opensearchdescription+xml",
      "title": "OpenSearch Description Document"
    },
    {
      "rel": "describedby",
      "href": "http://due.esrin.esa.int/page_project134.php",
  

Display the features on the map.


In [65]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 71**  
>  Representation: GeoJSON (OGC 17-069r3)   
> Requirement:  ERGO-CCAT-IF-031514  
>  Kind: EO Collection  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/geo+json;profile="http://www.opengis.net/spec/ogcapi-features-1/1.0"'
> ```


In [66]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/geo+json;profile="http://www.opengis.net/spec/ogcapi-features-1/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": {
    "coordinates": [
      [
        [
          -100,
          -50
        ],
        [
          160,
          -50
        ],
        [
          160,
          40
        ],
        [
          -100,
          40
        ],
        [
          -100,
          -50
        ]
      ]
    ],
    "type": "Polygon"
  },
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/collections/series/items/TropForest",
      "type": "application/geo+json"
    },
    {
      "rel": "collection",
      "href": "https://eovoc.spacebel.be/collections/series",
      "type": "application/json",
      "title": "the collection document"
    },
    {
      "rel": "search",
      "href": "https://eovoc.spacebel.be/collections/series/items/TropForest/api",
      "type": "application/opensearchdescription+xml",
      "title": "OpenSearch Description Document"
    },
    {
      "rel": "describedby",
      "href": "http://due.esrin.esa.int/page_project134.php",
  

Display the features on the map.


In [67]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 73**  
>  Representation: GeoJSON (OGC 17-084r1)   
> Requirement:  ERGO-CCAT-IF-031512  
>  Kind: EO Collection  
 NOT OK - does return OGC 17-069r3 instead.  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/geo+json;profile="http://www.opengis.net/spec/eoc-geojson/1.0"'
> ```


In [68]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/geo+json;profile="http://www.opengis.net/spec/eoc-geojson/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": {
    "coordinates": [
      [
        [
          -100,
          -50
        ],
        [
          160,
          -50
        ],
        [
          160,
          40
        ],
        [
          -100,
          40
        ],
        [
          -100,
          -50
        ]
      ]
    ],
    "type": "Polygon"
  },
  "id": "https://eovoc.spacebel.be/collections/series/items/TropForest?mode=owc",
  "type": "Feature",
  "properties": {
    "date": "2009-01-27T00:00:00.000Z/2011-08-09T23:59:59.999Z",
    "identifier": "TropForest",
    "contactPoint": [
      {
        "hasAddress": {
          "postal-code": "00044",
          "street-address": "Largo Galileo Galilei 1",
          "locality": "Frascati (Roma)",
          "country-name": "Italy"
        },
        "phone": "tel:+3906941801",
        "name": "ESA/ESRIN",
        "type": "Organization",
        "uri": "http://www.esa.int",
        "email": "eohelp@esa.int"
      }
    ],
    "kind": "http://purl.org/dc

Display the features on the map.


In [69]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 75**  
>  Representation: GeoJSON (OGC 17-084r1)   
> Requirement:  ERGO-CCAT-IF-031512/28  
>  Kind: EO Collection  
 OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/geo+json;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [70]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/geo+json;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": {
    "coordinates": [
      [
        [
          -100,
          -50
        ],
        [
          160,
          -50
        ],
        [
          160,
          40
        ],
        [
          -100,
          40
        ],
        [
          -100,
          -50
        ]
      ]
    ],
    "type": "Polygon"
  },
  "id": "https://eovoc.spacebel.be/collections/series/items/TropForest?mode=owc",
  "type": "Feature",
  "properties": {
    "date": "2009-01-27T00:00:00.000Z/2011-08-09T23:59:59.999Z",
    "identifier": "TropForest",
    "contactPoint": [
      {
        "hasAddress": {
          "postal-code": "00044",
          "street-address": "Largo Galileo Galilei 1",
          "locality": "Frascati (Roma)",
          "country-name": "Italy"
        },
        "phone": "tel:+3906941801",
        "name": "ESA/ESRIN",
        "type": "Organization",
        "uri": "http://www.esa.int",
        "email": "eohelp@esa.int"
      }
    ],
    "kind": "http://purl.org/dc

Display the features on the map.


In [71]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 77**  
>  Representation: GeoJSON (OGC 17-084r1/OGC 14-055r2)   
> Requirement:  ERGO-CCAT-IF-???  
>  Kind: EO Collection  
 NOT OK - Future work  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/geo+json;profile="http://www.opengis.net/spec/owc-geojson/1.0/req/core"'
> ```


In [72]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/geo+json;profile="http://www.opengis.net/spec/owc-geojson/1.0/req/core"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": {
    "coordinates": [
      [
        [
          -100,
          -50
        ],
        [
          160,
          -50
        ],
        [
          160,
          40
        ],
        [
          -100,
          40
        ],
        [
          -100,
          -50
        ]
      ]
    ],
    "type": "Polygon"
  },
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/collections/series/items/TropForest",
      "type": "application/geo+json"
    },
    {
      "rel": "collection",
      "href": "https://eovoc.spacebel.be/collections/series",
      "type": "application/json",
      "title": "the collection document"
    },
    {
      "rel": "search",
      "href": "https://eovoc.spacebel.be/collections/series/items/TropForest/api",
      "type": "application/opensearchdescription+xml",
      "title": "OpenSearch Description Document"
    },
    {
      "rel": "describedby",
      "href": "http://due.esrin.esa.int/page_project134.php",
  

Display the features on the map.


In [73]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 79**  
>  Representation: GeoJSON (OGC 17-084r1/OWC)   
> Requirement:  ERGO-CCAT-IF-031512  
>  Kind: EO Collection  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest?mode=owc' -H 'Accept: application/geo+json'
> ```


In [74]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest?mode=owc', headers={'Accept': 'application/geo+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": {
    "coordinates": [
      [
        [
          -100,
          -50
        ],
        [
          160,
          -50
        ],
        [
          160,
          40
        ],
        [
          -100,
          40
        ],
        [
          -100,
          -50
        ]
      ]
    ],
    "type": "Polygon"
  },
  "id": "https://eovoc.spacebel.be/collections/series/items/TropForest?mode=owc",
  "type": "Feature",
  "properties": {
    "date": "2009-01-27T00:00:00.000Z/2011-08-09T23:59:59.999Z",
    "identifier": "TropForest",
    "contactPoint": [
      {
        "hasAddress": {
          "postal-code": "00044",
          "street-address": "Largo Galileo Galilei 1",
          "locality": "Frascati (Roma)",
          "country-name": "Italy"
        },
        "phone": "tel:+3906941801",
        "name": "ESA/ESRIN",
        "type": "Organization",
        "uri": "http://www.esa.int",
        "email": "eohelp@esa.int"
      }
    ],
    "kind": "http://purl.org/dc

Display the features on the map.


In [75]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 81**  
>  Representation: GeoJSON (STAC)   
> Requirement:  ERGO-CCAT-IF-031516 ?  
>  Kind: EO Collection  
 NOT OK: should return an HTTP error as combination is not possible for collection (should be JSON).  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/geo+json;profile="https://stacspec.org"'
> ```


In [76]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/geo+json;profile="https://stacspec.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -100,
          -50,
          160,
          40
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          "2009-01-27T00:00:00.000Z",
          "2011-08-09T23:59:59.999Z"
        ]
      ]
    }
  },
  "stac_version": "1.0.0-rc.2",
  "keywords": [
    "Multi-mission collection",
    "JRC",
    "Food and Agriculture Organization (FAO)",
    "South East Asia",
    "South America",
    "DE1 663 km;  KO2 685 km; AL1 692 km",
    "DE1 625 km; KO2 15 km; AL1 70 km",
    "VIS (0.40 - 0.75 \u00b5m)",
    "NIR (0.75 - 1.30 \u00b5m)",
    "Sun-synchronous",
    "Very High Resolution - VHR (0 - 5m)",
    "High Resolution - HR (5 - 20 m)",
    "AL1_AV2_2F",
    "DE1_SL6_2F",
    "KO2_MSC_2F",
    "EARTH SCIENCE > AGRICULTURE",
    "EARTH SCIENCE > BIOSPHERE > ECOSYSTEMS > TERRESTRIAL ECOSYSTEMS",
    "EARTH SCIENCE > LAND SURFACE",
    "EARTH SCIENCE > BIOSPHERE > VEGETATION",
    "Agriculture",
    "For

Display the features on the map.


In [77]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 83**  
>  Representation: JSON (STAC)   
> Requirement:  ERGO-CCAT-IF-031526   
>  Kind: EO Collection  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/json;profile="https://stacspec.org"'
> ```


In [78]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/json;profile="https://stacspec.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": {
    "coordinates": [
      [
        [
          -100,
          -50
        ],
        [
          160,
          -50
        ],
        [
          160,
          40
        ],
        [
          -100,
          40
        ],
        [
          -100,
          -50
        ]
      ]
    ],
    "type": "Polygon"
  },
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/collections/series/items/TropForest",
      "type": "application/geo+json"
    },
    {
      "rel": "collection",
      "href": "https://eovoc.spacebel.be/collections/series",
      "type": "application/json",
      "title": "the collection document"
    },
    {
      "rel": "search",
      "href": "https://eovoc.spacebel.be/collections/series/items/TropForest/api",
      "type": "application/opensearchdescription+xml",
      "title": "OpenSearch Description Document"
    },
    {
      "rel": "describedby",
      "href": "http://due.esrin.esa.int/page_project134.php",
  

**Example: 84**  
>  Representation: JSON (default)   
> Requirement:  ERGO-CCAT-IF-031526   
>  Kind: EO Collection  
 NOT OK: returns GeoJSON instead of JSON  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/json'
> ```


In [79]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "extent": {
    "spatial": {
      "bbox": [
        [
          -100,
          -50,
          160,
          40
        ]
      ]
    },
    "temporal": {
      "interval": [
        [
          "2009-01-27T00:00:00.000Z",
          "2011-08-09T23:59:59.999Z"
        ]
      ]
    }
  },
  "stac_version": "1.0.0-rc.2",
  "keywords": [
    "Multi-mission collection",
    "JRC",
    "Food and Agriculture Organization (FAO)",
    "South East Asia",
    "South America",
    "DE1 663 km;  KO2 685 km; AL1 692 km",
    "DE1 625 km; KO2 15 km; AL1 70 km",
    "VIS (0.40 - 0.75 \u00b5m)",
    "NIR (0.75 - 1.30 \u00b5m)",
    "Sun-synchronous",
    "Very High Resolution - VHR (0 - 5m)",
    "High Resolution - HR (5 - 20 m)",
    "AL1_AV2_2F",
    "DE1_SL6_2F",
    "KO2_MSC_2F",
    "EARTH SCIENCE > AGRICULTURE",
    "EARTH SCIENCE > BIOSPHERE > ECOSYSTEMS > TERRESTRIAL ECOSYSTEMS",
    "EARTH SCIENCE > LAND SURFACE",
    "EARTH SCIENCE > BIOSPHERE > VEGETATION",
    "Agriculture",
    "For

**Example: 85**  
>  Representation: JSON-LD (default=OGC??)   
> Requirement:  EOVOC-CCAT-IF-031528  
>  Kind: EO Collection  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/ld+json'
> ```


In [80]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/ld+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:modified": "2019-05-23T00:00:00.000Z",
  "dcat:keyword": [
    "Multi-mission collection",
    "JRC",
    "Food and Agriculture Organization (FAO)",
    "South East Asia",
    "South America"
  ],
  "dct:spatial": {
    "@type": "dct:Location",
    "locn:geometry": [
      {
        "@value": "{\"type\":\"Polygon\",\"coordinates\":[[[-100,-50],[160,-50],[160,40],[-100,40],[-100,-50]]] }",
        "@type": "gsp:geoJSONLiteral"
      },
      {
        "@value": "POLYGON((-100.0 -50.0,160.0 -50.0,160.0 40.0,-100.0 40.0,-100.0 -50.0))",
        "@type": "gsp:wktLiteral"
      },
      {
        "@value": "<gml:Envelope srsName=\"http://www.opengis.net/def/crs/OGC/1.3/CRS84\"><gml:lowerCorner>-100.0 -50.0</gml:lowerCorner><gml:upperCorner>160.0 40.0</gml:upperCorner></gml:Envelope>",
        "@type": "gsp:gmlLiteral"
      }
    ]
  },
  "prov:wasGeneratedBy": [
    {
      "prov:used": [
        {
          "@type": "prov:Entity",
          "@id": "https://earth.esa.int/concept/a

**Example: 86**  
>  Representation: JSON-LD (OGC)   
> Requirement:  EOVOC-CCAT-IF-031528  
>  Kind: EO Collection  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/ld+json;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [81]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/ld+json;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:modified": "2019-05-23T00:00:00.000Z",
  "dct:date": "2009-01-27T00:00:00.000Z/2011-08-09T23:59:59.999Z",
  "dcat:keyword": [
    "Multi-mission collection",
    "JRC",
    "Food and Agriculture Organization (FAO)",
    "South East Asia",
    "South America"
  ],
  "dct:accessRights": [
    {
      "rdfs:label": "Data Available on EOCAT https://eocat.esa.int/sec/#data-services-area/search?osParameters={%22EOCAT-TropForest%22:%22%22,%22commonCriteria%22:%22bbox=-180,-90,180,90%22}",
      "@type": "dct:RightsStatement"
    }
  ],
  "prov:wasGeneratedBy": [
    {
      "prov:used": [
        {
          "eop:instrumentShortName": "AVNIR-2",
          "@type": "eop:Instrument",
          "@id": "https://earth.esa.int/concept/avnir-2"
        },
        {
          "eop:platformShortName": "ALOS-1",
          "@type": "eop:Platform",
          "@id": "https://earth.esa.int/concept/alos-1"
        }
      ],
      "@type": "prov:Activity"
    },
    {
      "prov:used": [
        {

**Example: 87**  
>  Representation: JSON-LD (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031530  
>  Kind: EO Collection  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/ld+json;profile="http://data.europa.eu/930/"'
> ```


In [82]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/ld+json;profile="http://data.europa.eu/930/"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:modified": "2019-05-23T00:00:00.000Z",
  "dcat:keyword": [
    "Multi-mission collection",
    "JRC",
    "Food and Agriculture Organization (FAO)",
    "South East Asia",
    "South America"
  ],
  "dct:spatial": {
    "@type": "dct:Location",
    "locn:geometry": [
      {
        "@value": "{\"type\":\"Polygon\",\"coordinates\":[[[-100,-50],[160,-50],[160,40],[-100,40],[-100,-50]]] }",
        "@type": "gsp:geoJSONLiteral"
      },
      {
        "@value": "POLYGON((-100.0 -50.0,160.0 -50.0,160.0 40.0,-100.0 40.0,-100.0 -50.0))",
        "@type": "gsp:wktLiteral"
      },
      {
        "@value": "<gml:Envelope srsName=\"http://www.opengis.net/def/crs/OGC/1.3/CRS84\"><gml:lowerCorner>-100.0 -50.0</gml:lowerCorner><gml:upperCorner>160.0 40.0</gml:upperCorner></gml:Envelope>",
        "@type": "gsp:gmlLiteral"
      }
    ]
  },
  "prov:wasGeneratedBy": [
    {
      "prov:used": [
        {
          "@type": "prov:Entity",
          "@id": "https://earth.esa.int/concept/a

**Example: 88**  
>  Representation: JSON-LD (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031532  
>  Kind: EO Collection  
  TBD   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/ld+json;profile="https://schema.org"'
> ```


In [83]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/ld+json;profile="https://schema.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "identifier": [
    "TropForest"
  ],
  "creator": [
    {
      "address": {
        "addressCountry": "Italy",
        "streetAddress": "Largo Galileo Galilei 1",
        "@type": "PostalAddress",
        "postalCode": "00044",
        "addressLocality": "Frascati (Roma)"
      },
      "@type": "Organization",
      "name": "ESA/ESRIN",
      "telephone": "tel:+3906941801",
      "url": "http://www.esa.int",
      "email": "eohelp@esa.int",
      "sameAs": [
        "https://gcmd.earthdata.nasa.gov/kms/concept/c56b4a86-82f8-4f15-98ba-c5f7abe8ee5a",
        "https://yago-knowledge.org/resource/European_Space_Agency",
        "https://dbpedia.org/resource/European_Space_Agency",
        "https://ror.org/03wd9za21"
      ]
    }
  ],
  "additionalProperty": [
    {
      "@type": "PropertyValue",
      "propertyID": "https://earth.esa.int/eop-ext/orbitHeight",
      "value": "DE1 663 km;  KO2 685 km; AL1 692 km"
    },
    {
      "@type": "PropertyValue",
      "propertyID": "http

**Example: 89**  
>  Representation: RDF/XML (default=OGC??)   
> Requirement:  EOVOC-CCAT-IF-031534  
>  Kind: EO Collection  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/rdf+xml'
> ```


In [84]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/rdf+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:Dataset rdf:about="https://eovoc.spacebel.be/collections/

**Example: 90**  
>  Representation: RDF/XML (OGC)   
> Requirement:  EOVOC-CCAT-IF-031534  
>  Kind: EO Collection  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/rdf+xml;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [85]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/rdf+xml;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:geo="http://a9.com/-/opensearch/extensions/geo/1.0/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:eop="http://www.opengis.net/ont/eo-geojson/1.0/" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#" xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:eo="http://a9.com/-/opensearch/extensions/eo/1.0/" xmlns:sru="http://a9.com/-/opensearch/extensions/sru/2.0/" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:gj="https://purl.org/geojson/vocab#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:time="http://a9.com/-/opensearch/extensions/time/1.0/" xmlns:owl="http://www.w3.org/2002/07/owl

**Example: 91**  
>  Representation: RDF/XML (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031536  
>  Kind: EO Collection  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/rdf+xml;profile="http://data.europa.eu/930/"'
> ```


In [86]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/rdf+xml;profile="http://data.europa.eu/930/"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:Dataset rdf:about="https://eovoc.spacebel.be/collections/

**Example: 92**  
>  Representation: RDF/XML (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031538  
>  Kind: EO Collection  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: application/rdf+xml;profile="https://schema.org"'
> ```


In [87]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'application/rdf+xml;profile="https://schema.org"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:schema="https://schema.org/" xmlns:wikidata="http://www.wikidata.org/entity/" xmlns:rdfa="http://www.w3.org/ns/rdfa#" xmlns:snomed="http://purl.bioontology.org/ontology/SNOMEDCT/" xmlns:yago="http://yago-knowledge.org/resource/" xmlns:dbpedia="http://dbpedia.org/resource/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:void="http://rdfs.org/ns/void#" xmlns:dcterms="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:dctype="http://purl.org/dc/dcmitype/" xmlns:eli="http://data.europa.eu/eli/ontology#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:bibo="http://purl.org/ontology/bibo/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <schema:Dataset rdf:about="https://eovoc.spacebel.be/collections/series/items/TropForest">


**Example: 93**  
>  Representation: Turtle (default=OGC??)   
> Requirement:  EOVOC-CCAT-IF-031540  
>  Kind: EO Collection  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: text/turtle'
> ```


In [88]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'text/turtle'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://earth.esa.int/eogateway/docum

**Example: 94**  
>  Representation: Turtle (OGC)   
> Requirement:  EOVOC-CCAT-IF-031540  
>  Kind: EO Collection  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: text/turtle;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [89]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'text/turtle;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix gj:    <https://purl.org/geojson/vocab#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix eop:   <http://www.opengis.net/ont/eo-geojson/1.0/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix eo:    <http://a9.com/-/opensearch/extensions/eo/1.0/> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix geo:   <http://a9.com/-/opensearch/extensions/geo/1.0/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix sru:   <http://a9.com/-/opensearch/extensions/sru/2.0/> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix time:  <http://a9.com/-/opensearch/extensions/time

**Example: 95**  
>  Representation: Turtle (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031542  
>  Kind: EO Collection  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: text/turtle;profile="http://data.europa.eu/930/"'
> ```


In [90]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'text/turtle;profile="http://data.europa.eu/930/"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://earth.esa.int/eogateway/docum

**Example: 96**  
>  Representation: Turtle (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031544  
>  Kind: EO Collection  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: text/turtle;profile="https://schema.org"'
> ```


In [91]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'text/turtle;profile="https://schema.org"'})
print(response.text)


@prefix schema: <https://schema.org/> .
@prefix void:  <http://rdfs.org/ns/void#> .
@prefix eli:   <http://data.europa.eu/eli/ontology#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix snomed: <http://purl.bioontology.org/ontology/SNOMEDCT/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix yago:  <http://yago-knowledge.org/resource/> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix dbpedia: <http://dbpedia.org/resource/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix rdf:   <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dctype: <http://purl.org/dc/dcmitype/> .
@prefix rdfa:  <http://www.w3.org/ns/rdfa#> .
@prefix dcterms: <http://purl.org/dc/terms/> .
@prefix bibo:  <http://purl.org/ontology/bibo/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix wikidata: <http://www.wikidata.org/entity/> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl

**Example: 97**  
>  Representation: text/html   
> Requirement:  EOVOC-CCAT-IF-0335410  
>  Kind: EO Collection  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/series/items/TropForest' -H 'Accept: text/html'
> ```


In [92]:
response = requests.get('https://eovoc.spacebel.be/collections/series/items/TropForest', headers={'Accept': 'text/html'})
print(response.text)


<html>
	<head>
                <title>FedEO Clearinghouse - TropForest</title>
                <meta name="viewport" content="width=device-width, initial-scale=1.0">
		<meta content="text/html; charset=UTF-8" http-equiv="content-type"/>
		<link rel="stylesheet" type="text/css" href="https://eovoc.spacebel.be/css/default.css"/>
                <script type="application/ld+json">
{
  "identifier": ["TropForest"],
  "creator": [{
    "address": {
      "addressCountry": "Italy",
      "streetAddress": "Largo Galileo Galilei 1",
      "@type": "PostalAddress",
      "postalCode": "00044",
      "addressLocality": "Frascati (Roma)"
    },
    "@type": "Organization",
    "name": "ESA/ESRIN",
    "telephone": "tel:+3906941801",
    "url": "http://www.esa.int",
    "email": "eohelp@esa.int",
    "sameAs": [
      "https://gcmd.earthdata.nasa.gov/kms/concept/c56b4a86-82f8-4f15-98ba-c5f7abe8ee5a",
      "https://yago-knowledge.org/resource/European_Space_Agency",
      "https://dbpedia.org/reso

<a name='Feature--EO-Service'></a>     
### Feature (EO Service)  
 The representations available for an EO Service include but are not limited to:
 * ISO19139
 * OGC 19-020r1
 * GeoDCAT-AP
 * Schema.org
 * HTML
    
   
   
**Example: 98**  
>  Representation: GeoJSON (default=OGC 17-069r3)   
> Requirement:  ERGO-CCAT-IF-031514  
>  Kind: EO Service  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/geo+json'
> ```


In [93]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/geo+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": null,
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/collections/services/items/rasdaman",
      "type": "application/geo+json"
    },
    {
      "rel": "collection",
      "href": "https://eovoc.spacebel.be/collections/services",
      "type": "application/json",
      "title": "the collection document"
    },
    {
      "rel": "profile",
      "href": "http://www.opengis.net/spec/owc-geojson/1.0/req/core"
    },
    {
      "rel": "profile",
      "href": "http://www.opengis.net/spec/eopad-geojson/1.0/req/core"
    },
    {
      "rel": "describedby",
      "href": "http://www.rasdaman.org/",
      "type": "text/html",
      "title": "Welcome to rasdaman \u2014 the world's most flexible and scalable Array / Datacube Engine"
    },
    {
      "rel": "alternate",
      "href": "https://eovoc.spacebel.be/collections/services/items/rasdaman?httpAccept=application/atom%2Bxml",
      "type": "application/atom+xml",
      "title": "Atom f

Display the features on the map.


In [94]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 100**  
>  Representation: GeoJSON (OGC 17-069r3)   
> Requirement:  ERGO-CCAT-IF-031514  
>  Kind: EO Service  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/geo+json;profile="http://www.opengis.net/spec/ogcapi-features-1/1.0"'
> ```


In [95]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/geo+json;profile="http://www.opengis.net/spec/ogcapi-features-1/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": null,
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/collections/services/items/rasdaman",
      "type": "application/geo+json"
    },
    {
      "rel": "collection",
      "href": "https://eovoc.spacebel.be/collections/services",
      "type": "application/json",
      "title": "the collection document"
    },
    {
      "rel": "profile",
      "href": "http://www.opengis.net/spec/owc-geojson/1.0/req/core"
    },
    {
      "rel": "profile",
      "href": "http://www.opengis.net/spec/eopad-geojson/1.0/req/core"
    },
    {
      "rel": "describedby",
      "href": "http://www.rasdaman.org/",
      "type": "text/html",
      "title": "Welcome to rasdaman \u2014 the world's most flexible and scalable Array / Datacube Engine"
    },
    {
      "rel": "alternate",
      "href": "https://eovoc.spacebel.be/collections/services/items/rasdaman?httpAccept=application/atom%2Bxml",
      "type": "application/atom+xml",
      "title": "Atom f

Display the features on the map.


In [96]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 102**  
>  Representation: GeoJSON (OGC 17-084r1)   
> Requirement:  ERGO-CCAT-IF-031512  
>  Kind: EO Service  
 NOT OK - does return OGC 17-069r3 instead.  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/geo+json;profile="http://www.opengis.net/spec/eopad-geojson/1.0"'
> ```


In [97]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/geo+json;profile="http://www.opengis.net/spec/eopad-geojson/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": null,
  "id": "https://eovoc.spacebel.be/collections/services/items/rasdaman?mode=owc",
  "type": "Feature",
  "properties": {
    "identifier": "rasdaman",
    "contactPoint": [
      {
        "name": "rasdaman GmbH",
        "type": "Organization",
        "uri": "http://rasdaman.org"
      }
    ],
    "kind": "http://purl.org/dc/dcmitype/Service",
    "abstract": "Rasdaman (raster data manager) is an open source array database system, which provides flexible, fast, scalable geo services for multi-dimensional spatio-temporal sensor, image, simulation, and statistics data of unlimited volume. ... data with all geo data in the PostgreSQL database, support for the raster-relevant OGC standards, Reference Implementation for WCS Core and WCPS.",
    "versionInfo": "9.5",
    "title": "rasdaman - raster data manager",
    "links": {
      "profiles": [
        {
          "href": "http://www.opengis.net/spec/owc-geojson/1.0/req/core"
        },
        {
          "href":

Display the features on the map.


In [98]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 104**  
>  Representation: GeoJSON (OGC 17-084r1)   
> Requirement:  ERGO-CCAT-IF-031512  
>  Kind: EO Service  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman?mode=owc' -H 'Accept: application/geo+json'
> ```


In [99]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman?mode=owc', headers={'Accept': 'application/geo+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "geometry": null,
  "id": "https://eovoc.spacebel.be/collections/services/items/rasdaman?mode=owc",
  "type": "Feature",
  "properties": {
    "identifier": "rasdaman",
    "contactPoint": [
      {
        "name": "rasdaman GmbH",
        "type": "Organization",
        "uri": "http://rasdaman.org"
      }
    ],
    "kind": "http://purl.org/dc/dcmitype/Service",
    "abstract": "Rasdaman (raster data manager) is an open source array database system, which provides flexible, fast, scalable geo services for multi-dimensional spatio-temporal sensor, image, simulation, and statistics data of unlimited volume. ... data with all geo data in the PostgreSQL database, support for the raster-relevant OGC standards, Reference Implementation for WCS Core and WCPS.",
    "versionInfo": "9.5",
    "title": "rasdaman - raster data manager",
    "links": {
      "profiles": [
        {
          "href": "http://www.opengis.net/spec/owc-geojson/1.0/req/core"
        },
        {
          "href":

Display the features on the map.


In [100]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 106**  
>  Representation: JSON-LD (default=schema.org??)   
> Requirement:  EOVOC-CCAT-IF-031528  
>  Kind: EO Service  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/ld+json'
> ```


In [101]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/ld+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:modified": "2018-01-31T00:00:55.511Z",
  "dcat:keyword": [
    "Big Data",
    "arrays",
    "raster data",
    "OGC",
    "WMS",
    "WCS",
    "WCS-T",
    "WCPS",
    "fast",
    "scalable",
    "flexible",
    "open standards",
    "free",
    "cost-efficient",
    "sensor",
    "image",
    "simulation",
    "statistics data"
  ],
  "foaf:isPrimaryTopicOf": {
    "dct:modified": "2021-10-20T16:12:55.511Z",
    "@type": "dcat:CatalogRecord",
    "dct:identifier": "https://eovoc.spacebel.be/collections/services/items/rasdaman",
    "dct:source": {
      "@type": "dcat:CatalogRecord",
      "@id": "https://eovoc.spacebel.be/collections/services/items/rasdaman?httpAccept=application/vnd.iso.19139-2%2Bxml",
      "dct:conformsTo": {
        "@type": "dct:Standard",
        "dct:title": "ISO19139"
      }
    },
    "dct:conformsTo": "https://joinup.ec.europa.eu/release/geodcat-ap/20"
  },
  "@type": "dcat:DataService",
  "dct:type": "http://inspire.ec.europa.eu/metadata-codeli

**Example: 107**  
>  Representation: JSON-LD (OGC)   
> Requirement:  EOVOC-CCAT-IF-031528  
>  Kind: EO Service  
 NOT OK - wrong mediatype (GeoJSON)  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/ld+json;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [102]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/ld+json;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:modified": "2018-01-31T00:00:55.511Z",
  "dct:date": "",
  "dcat:keyword": [
    "Big Data",
    "arrays",
    "raster data",
    "OGC",
    "WMS",
    "WCS",
    "WCS-T",
    "WCPS",
    "fast",
    "scalable",
    "flexible",
    "open standards",
    "free",
    "cost-efficient",
    "sensor",
    "image",
    "simulation",
    "statistics data"
  ],
  "foaf:isPrimaryTopicOf": {
    "dct:modified": "2021-10-20T16:12:55.511Z",
    "dct:created": "2021-10-20T16:12:55.511Z",
    "@type": "dcat:CatalogRecord",
    "dct:source": {
      "@type": "dcat:CatalogRecord",
      "dct:conformsTo": {
        "@type": "dct:Standard",
        "dct:title": "ISO19139"
      }
    },
    "dct:conformsTo": {
      "@type": "dct:Standard",
      "dct:title": "OGC 17-084r1",
      "owl:versionInfo": "r1"
    },
    "dct:language": {
      "@id": "http://id.loc.gov/vocabulary/iso639-1/en"
    }
  },
  "@type": "dcat:DataService",
  "dct:type": {
    "@id": "http://purl.org/dc/dcmitype/Service"
 

**Example: 108**  
>  Representation: JSON-LD (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031530  
>  Kind: EO Service  
 NOK:  adms:Identifier should have an uppercase when used as @type.  Wrong vcard namespace.  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/ld+json;profile="http://data.europa.eu/930/"'
> ```


In [103]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/ld+json;profile="http://data.europa.eu/930/"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:modified": "2018-01-31T00:00:55.511Z",
  "dcat:keyword": [
    "Big Data",
    "arrays",
    "raster data",
    "OGC",
    "WMS",
    "WCS",
    "WCS-T",
    "WCPS",
    "fast",
    "scalable",
    "flexible",
    "open standards",
    "free",
    "cost-efficient",
    "sensor",
    "image",
    "simulation",
    "statistics data"
  ],
  "foaf:isPrimaryTopicOf": {
    "dct:modified": "2021-10-20T16:12:55.511Z",
    "@type": "dcat:CatalogRecord",
    "dct:identifier": "https://eovoc.spacebel.be/collections/services/items/rasdaman",
    "dct:source": {
      "@type": "dcat:CatalogRecord",
      "@id": "https://eovoc.spacebel.be/collections/services/items/rasdaman?httpAccept=application/vnd.iso.19139-2%2Bxml",
      "dct:conformsTo": {
        "@type": "dct:Standard",
        "dct:title": "ISO19139"
      }
    },
    "dct:conformsTo": "https://joinup.ec.europa.eu/release/geodcat-ap/20"
  },
  "@type": "dcat:DataService",
  "dct:type": "http://inspire.ec.europa.eu/metadata-codeli

**Example: 109**  
>  Representation: JSON-LD (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031532  
>  Kind: EO Service  
  OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/ld+json;profile="https://schema.org"'
> ```


In [104]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/ld+json;profile="https://schema.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "identifier": [
    "rasdaman",
    {
      "@type": "PropertyValue",
      "@id": "https://doi.org/10.5281/zenodo.1040170",
      "propertyID": "https://registry.identifiers.org/registry/doi",
      "value": "doi:10.5281/zenodo.1040170",
      "url": "https://doi.org/10.5281/zenodo.1040170"
    }
  ],
  "keywords": [
    {
      "@type": "DefinedTerm",
      "name": "EARTH SCIENCE SERVICES > DATA MANAGEMENT/DATA HANDLING > DATA ACCESS/RETRIEVAL",
      "@id": "https://gcmd.earthdata.nasa.gov/kms/concept/86cbb2d3-6783-4d9b-9dc1-b0aea78f98ea",
      "inDefinedTermSet": "https://gcmd.earthdata.nasa.gov/kms/concepts/concept_scheme/sciencekeywords"
    },
    {
      "@type": "DefinedTerm",
      "name": "OGC Web Coverage Service 2.0",
      "@id": "http://www.opengis.net/def/serviceType/ogc/wcs/2.0",
      "inDefinedTermSet": "https://inspire.ec.europa.eu/metadata-codelist/ProtocolValue"
    },
    {
      "@type": "DefinedTerm",
      "name": "Coverage access service",
      "@id": "

**Example: 110**  
>  Representation: RDF/XML (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031534  
>  Kind: EO Service  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/rdf+xml'
> ```


In [105]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/rdf+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:DataService rdf:about="https://eovoc.spacebel.be/collecti

**Example: 111**  
>  Representation: RDF/XML (OGC)   
> Requirement:  EOVOC-CCAT-IF-031534  
>  Kind: EO Service  
 NOT OK - wrong media type  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/rdf+xml;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [106]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/rdf+xml;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:geo="http://a9.com/-/opensearch/extensions/geo/1.0/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:eop="http://www.opengis.net/ont/eo-geojson/1.0/" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#" xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:eo="http://a9.com/-/opensearch/extensions/eo/1.0/" xmlns:sru="http://a9.com/-/opensearch/extensions/sru/2.0/" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:gj="https://purl.org/geojson/vocab#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:time="http://a9.com/-/opensearch/extensions/time/1.0/" xmlns:owl="http://www.w3.org/2002/07/owl

**Example: 112**  
>  Representation: RDF/XML (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031536  
>  Kind: EO Service  
 NOT OK: missing namespaces  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/rdf+xml;profile="http://data.europa.eu/930/"'
> ```


In [107]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/rdf+xml;profile="http://data.europa.eu/930/"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:DataService rdf:about="https://eovoc.spacebel.be/collecti

**Example: 113**  
>  Representation: RDF/XML (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031538  
>  Kind: EO Service  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: application/rdf+xml;profile="https://schema.org"'
> ```


In [108]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'application/rdf+xml;profile="https://schema.org"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:schema="https://schema.org/" xmlns:wikidata="http://www.wikidata.org/entity/" xmlns:rdfa="http://www.w3.org/ns/rdfa#" xmlns:snomed="http://purl.bioontology.org/ontology/SNOMEDCT/" xmlns:yago="http://yago-knowledge.org/resource/" xmlns:dbpedia="http://dbpedia.org/resource/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:void="http://rdfs.org/ns/void#" xmlns:dcterms="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:dctype="http://purl.org/dc/dcmitype/" xmlns:eli="http://data.europa.eu/eli/ontology#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:bibo="http://purl.org/ontology/bibo/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <schema:PropertyValue rdf:about="https://doi.org/10.5281/zenodo.1040170">
      
    
     

**Example: 114**  
>  Representation: Turtle (default=OGC??)   
> Requirement:  EOVOC-CCAT-IF-031540  
>  Kind: EO Service  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: text/turtle'
> ```


In [109]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'text/turtle'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<http://www.rasdaman.org/>
        a  

**Example: 115**  
>  Representation: Turtle (OGC)   
> Requirement:  EOVOC-CCAT-IF-031540  
>  Kind: EO Service  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: text/turtle;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [110]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'text/turtle;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix gj:    <https://purl.org/geojson/vocab#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix eop:   <http://www.opengis.net/ont/eo-geojson/1.0/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix eo:    <http://a9.com/-/opensearch/extensions/eo/1.0/> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix geo:   <http://a9.com/-/opensearch/extensions/geo/1.0/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix sru:   <http://a9.com/-/opensearch/extensions/sru/2.0/> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix time:  <http://a9.com/-/opensearch/extensions/time

**Example: 116**  
>  Representation: Turtle (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031542  
>  Kind: EO Service  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: text/turtle;profile="http://data.europa.eu/930/"'
> ```


In [111]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'text/turtle;profile="http://data.europa.eu/930/"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<http://www.rasdaman.org/>
        a  

**Example: 117**  
>  Representation: Turtle (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031544  
>  Kind: EO Service  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: text/turtle;profile="https://schema.org"'
> ```


In [112]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'text/turtle;profile="https://schema.org"'})
print(response.text)


@prefix schema: <https://schema.org/> .
@prefix void:  <http://rdfs.org/ns/void#> .
@prefix eli:   <http://data.europa.eu/eli/ontology#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix snomed: <http://purl.bioontology.org/ontology/SNOMEDCT/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix yago:  <http://yago-knowledge.org/resource/> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix dbpedia: <http://dbpedia.org/resource/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix rdf:   <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dctype: <http://purl.org/dc/dcmitype/> .
@prefix rdfa:  <http://www.w3.org/ns/rdfa#> .
@prefix dcterms: <http://purl.org/dc/terms/> .
@prefix bibo:  <http://purl.org/ontology/bibo/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix wikidata: <http://www.wikidata.org/entity/> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl

**Example: 118**  
>  Representation: text/html   
> Requirement:  EOVOC-CCAT-IF-0335410  
>  Kind: EO Service  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/services/items/rasdaman' -H 'Accept: text/html'
> ```


In [113]:
response = requests.get('https://eovoc.spacebel.be/collections/services/items/rasdaman', headers={'Accept': 'text/html'})
print(response.text)


<html>
	<head>
                <title>FedEO Clearinghouse - rasdaman</title>
                <meta name="viewport" content="width=device-width, initial-scale=1.0">
		<meta content="text/html; charset=UTF-8" http-equiv="content-type"/>
		<link rel="stylesheet" type="text/css" href="https://eovoc.spacebel.be/css/default.css"/>
                <script type="application/ld+json">
{
  "identifier": [
    "rasdaman",
    {
      "@type": "PropertyValue",
      "@id": "https://doi.org/10.5281/zenodo.1040170",
      "propertyID": "https://registry.identifiers.org/registry/doi",
      "value": "doi:10.5281/zenodo.1040170",
      "url": "https://doi.org/10.5281/zenodo.1040170"
    }
  ],
  "keywords": [
    {
      "@type": "DefinedTerm",
      "name": "EARTH SCIENCE SERVICES > DATA MANAGEMENT/DATA HANDLING > DATA ACCESS/RETRIEVAL",
      "@id": "https://gcmd.earthdata.nasa.gov/kms/concept/86cbb2d3-6783-4d9b-9dc1-b0aea78f98ea",
      "inDefinedTermSet": "https://gcmd.earthdata.nasa.gov/kms/conce

<a name='Feature--EO-Granule'></a>     
### Feature (EO Granule)  
 The representations available for an EO Granule include but are not limited to:
 * OGC 10-157r4
 * OGC 10-157r3
 * OGC 17-003r2
 * OGC 17-069r3
 * STAC Item
 * GeoDCAT-AP
 * Schema.org
 * HTML
    
   
   
**Example: 119**  
>  Representation: GeoJSON (default=OGC 17-069r3)   
> Requirement:  ERGO-CCAT-IF-031514  
>  Kind: EO Granule  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/geo+json'
> ```


In [114]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/geo+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "bbox": [
    4.25,
    51.15,
    4.51,
    51.33
  ],
  "geometry": {
    "coordinates": [
      [
        [
          4.32,
          51.33
        ],
        [
          4.51,
          51.31
        ],
        [
          4.47,
          51.15
        ],
        [
          4.25,
          51.19
        ],
        [
          4.32,
          51.33
        ]
      ]
    ],
    "type": "Polygon"
  },
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001",
      "type": "application/geo+json"
    },
    {
      "rel": "collection",
      "href": "https://eovoc.spacebel.be/collections/series/items/PROBA.CHRIS.1A?httpAccept=application/json",
      "type": "application/json",
      "title": "the collection document"
    },
    {
      "rel": "enclosure",
      "href": "https://tpm-ds.eo.esa.int/oads/data/PROBA1-CHRIS/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_00

Display the features on the map.


In [115]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 121**  
>  Representation: GeoJSON (OGC 17-069r3)   
> Requirement:  ERGO-CCAT-IF-031514  
>  Kind: EO Granule  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/geo+json;profile="http://www.opengis.net/spec/ogcapi-features-1/1.0"'
> ```


In [116]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/geo+json;profile="http://www.opengis.net/spec/ogcapi-features-1/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "bbox": [
    4.25,
    51.15,
    4.51,
    51.33
  ],
  "geometry": {
    "coordinates": [
      [
        [
          4.32,
          51.33
        ],
        [
          4.51,
          51.31
        ],
        [
          4.47,
          51.15
        ],
        [
          4.25,
          51.19
        ],
        [
          4.32,
          51.33
        ]
      ]
    ],
    "type": "Polygon"
  },
  "links": [
    {
      "rel": "self",
      "href": "https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001",
      "type": "application/geo+json"
    },
    {
      "rel": "collection",
      "href": "https://eovoc.spacebel.be/collections/series/items/PROBA.CHRIS.1A?httpAccept=application/json",
      "type": "application/json",
      "title": "the collection document"
    },
    {
      "rel": "enclosure",
      "href": "https://tpm-ds.eo.esa.int/oads/data/PROBA1-CHRIS/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_00

Display the features on the map.


In [117]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 123**  
>  Representation: GeoJSON (OGC 17-003r2)   
> Requirement:  ERGO-CCAT-IF-031512  
>  Kind: EO Granule  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/geo+json;profile="http://www.opengis.net/spec/eo-geojson/1.0"'
> ```


In [118]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/geo+json;profile="http://www.opengis.net/spec/eo-geojson/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "bbox": [
    4.25,
    51.15,
    4.51,
    51.33
  ],
  "geometry": {
    "coordinates": [
      [
        [
          4.32,
          51.33
        ],
        [
          4.51,
          51.31
        ],
        [
          4.47,
          51.15
        ],
        [
          4.25,
          51.19
        ],
        [
          4.32,
          51.33
        ]
      ]
    ],
    "type": "Polygon"
  },
  "id": "https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001?mode=owc",
  "type": "Feature",
  "properties": {
    "date": "2007-08-04T10:36:00Z/2007-08-04T10:40:00Z",
    "identifier": "PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001",
    "kind": "http://purl.org/dc/dcmitype/Dataset",
    "parentIdentifier": "PROBA.CHRIS.1A",
    "productInformation": {
      "referenceSystemIdentifier": "epsg:4326",
      "size": 132664189,
      "productType": "CHR_MO2_1P",
      "availabilityTime": "2007-08-04T10:40:00Z"
    }

Display the features on the map.


In [119]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 125**  
>  Representation: GeoJSON (OGC 17-003r2)   
> Requirement:  ERGO-CCAT-IF-031512  
>  Kind: EO Granule  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001?mode=owc'
> ```


In [120]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001?mode=owc', headers={'Accept': ''})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "bbox": [
    4.25,
    51.15,
    4.51,
    51.33
  ],
  "geometry": {
    "coordinates": [
      [
        [
          4.32,
          51.33
        ],
        [
          4.51,
          51.31
        ],
        [
          4.47,
          51.15
        ],
        [
          4.25,
          51.19
        ],
        [
          4.32,
          51.33
        ]
      ]
    ],
    "type": "Polygon"
  },
  "id": "https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001?mode=owc",
  "type": "Feature",
  "properties": {
    "date": "2007-08-04T10:36:00Z/2007-08-04T10:40:00Z",
    "identifier": "PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001",
    "kind": "http://purl.org/dc/dcmitype/Dataset",
    "parentIdentifier": "PROBA.CHRIS.1A",
    "productInformation": {
      "referenceSystemIdentifier": "epsg:4326",
      "size": 132664189,
      "productType": "CHR_MO2_1P",
      "availabilityTime": "2007-08-04T10:40:00Z"
    }

**Example: 126**  
>  Representation: GeoJSON (STAC)   
> Requirement:  ERGO-CCAT-IF-031516  
>  Kind: EO Granule  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/geo+json;profile="https://stacspec.org"'
> ```


In [121]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/geo+json;profile="https://stacspec.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "stac_version": "1.0.0-rc.2",
  "assets": {
    "thumbnail": {
      "roles": [
        "thumbnail"
      ],
      "href": "http://tpm-ds.eo.esa.int/oads/meta/PROBA1-CHRIS/browse/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001.SIP.ZIP_BID.PNG",
      "type": "image/png",
      "title": "QUICKLOOK"
    },
    "metadata_ogc_10_157r3": {
      "roles": [
        "metadata"
      ],
      "href": "https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001?httpAccept=application/gml%2Bxml&recordSchema=om10",
      "title": "OGC 10-157r3 metadata",
      "type": "application/gml+xml;profile=\"http://www.opengis.net/spec/EOMPOM/1.0\""
    },
    "enclosure": {
      "roles": [
        "data"
      ],
      "href": "https://tpm-ds.eo.esa.int/oads/data/PROBA1-CHRIS/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001.SIP.ZIP",
      "type": "application/x-binary",
      "title": "Download"
    },
    "metadata_ogc_10_157r4":

Display the features on the map.


In [122]:
show_features_on_map(response)


Map(center=[38.128, 2.588], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

**Example: 128**  
>  Representation: Atom   
> Requirement:  ERGO-CCAT-IF-031518  
>  Kind: EO Granule  
 NOT OK: Atom link alternate ends with ?nullnull  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/atom+xml'
> ```


In [123]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/atom+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<atom:feed xmlns:atom="http://www.w3.org/2005/Atom" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:eo="http://a9.com/-/opensearch/extensions/eo/1.0/" xmlns:geo="http://a9.com/-/opensearch/extensions/geo/1.0/" xmlns:georss="http://www.georss.org/georss" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:owc="http://www.opengis.net/owc/1.0" xmlns:referrer="http://a9.com/-/opensearch/extensions/referrer/1.0/" xmlns:semantic="http://a9.com/-/opensearch/extensions/semantic/1.0/" xmlns:sru="http://a9.com/-/opensearch/extensions/sru/2.0/" xmlns:time="http://a9.com/-/opensearch/extensions/time/1.0/">
   

   <atom:author>
      

      <atom:name>FedEO Clearinghouse</atom:name>
      

      <atom:email>eohelp@eo.esa.int</atom:email>
      

   </atom:author>
   

   <atom:generator>FedEO Clearinghouse</atom:generator>
   

   <atom:id>https://eovoc.spacebel.be/collections/datasets/items</atom:id>
   

   <atom:rights>Copyright 2016-2020, European Space Agency</ato

**Example: 129**  
>  Representation: JSON-LD (default)   
> Requirement:  EOVOC-CCAT-IF-031528  
>  Kind: EO Granule  
 TBD  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/ld+json'
> ```


In [124]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/ld+json'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:modified": "2021-09-14T14:04:11Z",
  "dct:spatial": {
    "@type": "dct:Location",
    "locn:geometry": [
      {
        "@value": "{\"type\":\"Polygon\",\"coordinates\":[[[4.32,51.33],[4.51,51.31],[4.47,51.15],[4.25,51.19],[4.32,51.33]]] }",
        "@type": "gsp:geoJSONLiteral"
      },
      {
        "@value": "POLYGON((4.32 51.33,4.51 51.31,4.47 51.15,4.25 51.19,4.32 51.33))",
        "@type": "gsp:wktLiteral"
      },
      {
        "@value": "<gml:Envelope srsName=\"http://www.opengis.net/def/crs/OGC/1.3/CRS84\"><gml:lowerCorner>4.25 51.15</gml:lowerCorner><gml:upperCorner>4.51 51.33</gml:upperCorner></gml:Envelope>",
        "@type": "gsp:gmlLiteral"
      }
    ]
  },
  "prov:wasGeneratedBy": [
    {
      "prov:used": [
        {
          "@type": "prov:Entity",
          "@id": "https://earth.esa.int/concept/chris",
          "dct:title": "CHRIS"
        },
        {
          "@type": "prov:Entity",
          "@id": "https://earth.esa.int/concept/proba-1",
     

**Example: 130**  
>  Representation: JSON-LD (OGC)   
> Requirement:  EOVOC-CCAT-IF-031528  
>  Kind: EO Granule  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/ld+json;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [125]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/ld+json;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:modified": "2021-09-14T14:04:11Z",
  "eop:productInformation": {
    "eop:productType": "CHR_MO2_1P",
    "eop:referenceSystemIdentifier": {
      "@id": "http://www.opengis.net/def/crs/EPSG/0/4326"
    },
    "eop:size": 132664189,
    "@type": "eop:ProductInformation",
    "eop:availabilityTime": "2007-08-04T10:40:00Z"
  },
  "gj:bbox": {
    "@list": [
      4.25,
      51.15,
      4.51,
      51.33
    ]
  },
  "dct:date": "2007-08-04T10:36:00Z/2007-08-04T10:40:00Z",
  "eop:parentIdentifier": "PROBA.CHRIS.1A",
  "dct:spatial": {
    "@type": "dct:Location",
    "locn:geometry": [
      {
        "@value": "{\"type\":\"Polygon\",\"coordinates\":[[[4.32,51.33],[4.51,51.31],[4.47,51.15],[4.25,51.19],[4.32,51.33]]] }",
        "@type": "gsp:geoJSONLiteral"
      },
      {
        "@value": "POLYGON((4.32 51.33,4.51 51.31,4.47 51.15,4.25 51.19,4.32 51.33))",
        "@type": "gsp:wktLiteral"
      },
      {
        "@value": "<gml:Envelope srsName=\"http://www.opengis.net/de

**Example: 131**  
>  Representation: JSON-LD (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031530  
>  Kind: EO Granule  
 NOK:  platform and instrument id are empty in prov:wasGeneratedby.  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/ld+json;profile="http://data.europa.eu/930/"'
> ```


In [126]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/ld+json;profile="http://data.europa.eu/930/"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "dct:modified": "2021-09-14T14:04:11Z",
  "dct:spatial": {
    "@type": "dct:Location",
    "locn:geometry": [
      {
        "@value": "{\"type\":\"Polygon\",\"coordinates\":[[[4.32,51.33],[4.51,51.31],[4.47,51.15],[4.25,51.19],[4.32,51.33]]] }",
        "@type": "gsp:geoJSONLiteral"
      },
      {
        "@value": "POLYGON((4.32 51.33,4.51 51.31,4.47 51.15,4.25 51.19,4.32 51.33))",
        "@type": "gsp:wktLiteral"
      },
      {
        "@value": "<gml:Envelope srsName=\"http://www.opengis.net/def/crs/OGC/1.3/CRS84\"><gml:lowerCorner>4.25 51.15</gml:lowerCorner><gml:upperCorner>4.51 51.33</gml:upperCorner></gml:Envelope>",
        "@type": "gsp:gmlLiteral"
      }
    ]
  },
  "prov:wasGeneratedBy": [
    {
      "prov:used": [
        {
          "@type": "prov:Entity",
          "@id": "https://earth.esa.int/concept/chris",
          "dct:title": "CHRIS"
        },
        {
          "@type": "prov:Entity",
          "@id": "https://earth.esa.int/concept/proba-1",
     

**Example: 132**  
>  Representation: JSON-LD (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031532  
>  Kind: EO Granule  
  OK   
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/ld+json;profile="https://schema.org"'
> ```


In [127]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/ld+json;profile="https://schema.org"'})
payload = json.loads(response.text)
print(json.dumps(payload,indent=2))


{
  "identifier": [
    "PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001"
  ],
  "keywords": [
    {
      "@type": "DefinedTerm",
      "name": "CHRIS",
      "@id": "https://earth.esa.int/concept/chris",
      "inDefinedTermSet": "https://earth.esa.int/concepts/concept_scheme/instruments"
    },
    {
      "@type": "DefinedTerm",
      "name": "PROBA-1",
      "@id": "https://earth.esa.int/concept/proba-1",
      "inDefinedTermSet": "https://earth.esa.int/concepts/concept_scheme/platforms"
    },
    {
      "@type": "DefinedTerm",
      "@id": "https://gcmd.earthdata.nasa.gov/kms/concept/fe4a4604-029e-4cdc-93f0-6d8799dd25e5",
      "inDefinedTermSet": "https://gcmd.earthdata.nasa.gov/kms/concepts/concept_scheme/platforms"
    },
    {
      "@type": "DefinedTerm",
      "@id": "http://dbpedia.org/resource/PROBA",
      "inDefinedTermSet": "http://dbpedia.org/resource/Satellite"
    },
    {
      "@type": "DefinedTerm",
      "@id": "http://www.wikidata.org/entity/Q147985

**Example: 133**  
>  Representation: RDF/XML (default)   
> Requirement:  EOVOC-CCAT-IF-031534  
>  Kind: EO Granule  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/rdf+xml'
> ```


In [128]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/rdf+xml'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:Dataset rdf:about="https://eovoc.spacebel.be/collections/

**Example: 134**  
>  Representation: RDF/XML (OGC)   
> Requirement:  EOVOC-CCAT-IF-031534  
>  Kind: EO Granule  
 NOT OK - wrong media type  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/rdf+xml;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [129]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/rdf+xml;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:geo="http://a9.com/-/opensearch/extensions/geo/1.0/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:eop="http://www.opengis.net/ont/eo-geojson/1.0/" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#" xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:j.0="ical:" xmlns:eo="http://a9.com/-/opensearch/extensions/eo/1.0/" xmlns:sru="http://a9.com/-/opensearch/extensions/sru/2.0/" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:gj="https://purl.org/geojson/vocab#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:time="http://a9.com/-/opensearch/extensions/time/1.0/" xmlns:owl="http://www.

**Example: 135**  
>  Representation: RDF/XML (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031536  
>  Kind: EO Granule  
 NOT OK: HTTP error 415  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/rdf+xml;profile="http://data.europa.eu/930/"'
> ```


In [130]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/rdf+xml;profile="http://data.europa.eu/930/"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:ldp="http://www.w3.org/ns/ldp#" xmlns:iana="http://www.iana.org/assignments/relation/" xmlns:locn="http://www.w3.org/ns/locn#" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:os="http://a9.com/-/spec/opensearch/1.1/" xmlns:void="http://rdfs.org/ns/void#" xmlns:dct="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:adms="http://www.w3.org/ns/adms#" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:prov="http://www.w3.org/ns/prov#" xmlns:vcard="http://www.w3.org/2006/vcard/ns#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:gsp="http://www.opengis.net/ont/geosparql#" xmlns:owc="http://www.opengis.net/ont/owc/1.0/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:atom="http://www.w3.org/2005/Atom/" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <dcat:Dataset rdf:about="https://eovoc.spacebel.be/collections/

**Example: 136**  
>  Representation: RDF/XML (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031538  
>  Kind: EO Granule  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: application/rdf+xml;profile="https://schema.org"'
> ```


In [131]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'application/rdf+xml;profile="https://schema.org"'})
xmlstr = minidom.parseString(response.text).toprettyxml(indent='   ')
print(xmlstr)


<?xml version="1.0" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#" xmlns:schema="https://schema.org/" xmlns:wikidata="http://www.wikidata.org/entity/" xmlns:rdfa="http://www.w3.org/ns/rdfa#" xmlns:snomed="http://purl.bioontology.org/ontology/SNOMEDCT/" xmlns:yago="http://yago-knowledge.org/resource/" xmlns:dbpedia="http://dbpedia.org/resource/" xmlns:rdfs="http://www.w3.org/2000/01/rdf-schema#" xmlns:void="http://rdfs.org/ns/void#" xmlns:dcterms="http://purl.org/dc/terms/" xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:owl="http://www.w3.org/2002/07/owl#" xmlns:dctype="http://purl.org/dc/dcmitype/" xmlns:eli="http://data.europa.eu/eli/ontology#" xmlns:skos="http://www.w3.org/2004/02/skos/core#" xmlns:bibo="http://purl.org/ontology/bibo/" xmlns:dcat="http://www.w3.org/ns/dcat#" xmlns:foaf="http://xmlns.com/foaf/0.1/" xmlns:xsd="http://www.w3.org/2001/XMLSchema#">
   
  
   <schema:Dataset rdf:about="https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CH

**Example: 137**  
>  Representation: Turtle (default=schema.org)   
> Requirement:  EOVOC-CCAT-IF-031540  
>  Kind: EO Granule  
 OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: text/turtle'
> ```


In [132]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'text/turtle'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://eovoc.spacebel.be/collections

**Example: 138**  
>  Representation: Turtle (OGC)   
> Requirement:  EOVOC-CCAT-IF-031540  
>  Kind: EO Granule  
 NOT OK: wrong media type  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: text/turtle;profile="http://www.opengis.net/spec/os-geojson/1.0"'
> ```


In [133]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'text/turtle;profile="http://www.opengis.net/spec/os-geojson/1.0"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix gj:    <https://purl.org/geojson/vocab#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix eop:   <http://www.opengis.net/ont/eo-geojson/1.0/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix eo:    <http://a9.com/-/opensearch/extensions/eo/1.0/> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix geo:   <http://a9.com/-/opensearch/extensions/geo/1.0/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix sru:   <http://a9.com/-/opensearch/extensions/sru/2.0/> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix time:  <http://a9.com/-/opensearch/extensions/time

**Example: 139**  
>  Representation: Turtle (DCAT)   
> Requirement:  EOVOC-CCAT-IF-031542  
>  Kind: EO Granule  
 NOT OK: HTTP 415 error  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: text/turtle;profile="http://data.europa.eu/930/"'
> ```


In [134]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'text/turtle;profile="http://data.europa.eu/930/"'})
print(response.text)


@prefix void:  <http://rdfs.org/ns/void#> .
@prefix os:    <http://a9.com/-/spec/opensearch/1.1/> .
@prefix adms:  <http://www.w3.org/ns/adms#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix gsp:   <http://www.opengis.net/ont/geosparql#> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix vcard: <http://www.w3.org/2006/vcard/ns#> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix ldp:   <http://www.w3.org/ns/ldp#> .
@prefix owc:   <http://www.opengis.net/ont/owc/1.0/> .
@prefix iana:  <http://www.iana.org/assignments/relation/> .
@prefix locn:  <http://www.w3.org/ns/locn#> .
@prefix atom:  <http://www.w3.org/2005/Atom/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix prov:  <http://www.w3.org/ns/prov#> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl.org/dc/elements/1.1/> .

<https://earth.esa.int/concept/proba-1

**Example: 140**  
>  Representation: Turtle (schema.org)   
> Requirement:  EOVOC-CCAT-IF-031544  
>  Kind: EO Granule  
  OK    
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: text/turtle;profile="https://schema.org"'
> ```


In [135]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'text/turtle;profile="https://schema.org"'})
print(response.text)


@prefix schema: <https://schema.org/> .
@prefix void:  <http://rdfs.org/ns/void#> .
@prefix eli:   <http://data.europa.eu/eli/ontology#> .
@prefix owl:   <http://www.w3.org/2002/07/owl#> .
@prefix snomed: <http://purl.bioontology.org/ontology/SNOMEDCT/> .
@prefix xsd:   <http://www.w3.org/2001/XMLSchema#> .
@prefix yago:  <http://yago-knowledge.org/resource/> .
@prefix skos:  <http://www.w3.org/2004/02/skos/core#> .
@prefix rdfs:  <http://www.w3.org/2000/01/rdf-schema#> .
@prefix dbpedia: <http://dbpedia.org/resource/> .
@prefix dct:   <http://purl.org/dc/terms/> .
@prefix rdf:   <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dctype: <http://purl.org/dc/dcmitype/> .
@prefix rdfa:  <http://www.w3.org/ns/rdfa#> .
@prefix dcterms: <http://purl.org/dc/terms/> .
@prefix bibo:  <http://purl.org/ontology/bibo/> .
@prefix dcat:  <http://www.w3.org/ns/dcat#> .
@prefix wikidata: <http://www.wikidata.org/entity/> .
@prefix foaf:  <http://xmlns.com/foaf/0.1/> .
@prefix dc:    <http://purl

**Example: 141**  
>  Representation: text/html   
> Requirement:  EOVOC-CCAT-IF-0335410  
>  Kind: EO Granule  
  OK  
> ```bash
> curl -v 'https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001' -H 'Accept: text/html'
> ```


In [136]:
response = requests.get('https://eovoc.spacebel.be/collections/datasets/items/PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001', headers={'Accept': 'text/html'})
print(response.text)


<html>
	<head>
                <title>FedEO Clearinghouse - PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001</title>
                <meta name="viewport" content="width=device-width, initial-scale=1.0">
		<meta content="text/html; charset=UTF-8" http-equiv="content-type"/>
		<link rel="stylesheet" type="text/css" href="https://eovoc.spacebel.be/css/default.css"/>
                <script type="application/ld+json">
{
  "identifier": ["PR1_OPER_CHR_MO2_1P_20070804T103600_N51-024_E004-004_0001"],
  "keywords": [
    {
      "@type": "DefinedTerm",
      "name": "CHRIS",
      "@id": "https://earth.esa.int/concept/chris",
      "inDefinedTermSet": "https://earth.esa.int/concepts/concept_scheme/instruments"
    },
    {
      "@type": "DefinedTerm",
      "name": "PROBA-1",
      "@id": "https://earth.esa.int/concept/proba-1",
      "inDefinedTermSet": "https://earth.esa.int/concepts/concept_scheme/platforms"
    },
    {
      "@type": "DefinedTerm",
      "@id": "https://gcmd.ea